In [1]:
# Librerie
import pandas as pd
import numpy as np
import json
from json import JSONDecoder
import re
import requests
NOT_WHITESPACE = re.compile(r'[^\s]')
from os import listdir, rename, system, getpid
from os.path import isfile, join
from collections import defaultdict
from time import gmtime, strftime
import ast
import time
from pympler.asizeof import asizeof
import sys
np.set_printoptions(threshold=sys.maxsize)
import multiprocessing as mp
import pickle
import collections
import operator

In [2]:
def get_size(obj, seen=None):
    """Recursively finds size of objects"""
    size = sys.getsizeof(obj)
    if seen is None:
        seen = set()
    obj_id = id(obj)
    if obj_id in seen:
        return 0
    # Important mark as seen *before* entering recursion to gracefully handle
    # self-referential objects
    seen.add(obj_id)
    if isinstance(obj, dict):
        size += sum([get_size(v, seen) for v in obj.values()])
        size += sum([get_size(k, seen) for k in obj.keys()])
    elif hasattr(obj, '__dict__'):
        size += get_size(obj.__dict__, seen)
    elif hasattr(obj, '__iter__') and not isinstance(obj, (str, bytes, bytearray)):
        size += sum([get_size(i, seen) for i in obj])
    return size

In [3]:
class color:
   PURPLE = '\033[95m'
   CYAN = '\033[96m'
   DARKCYAN = '\033[36m'
   BLUE = '\033[94m'
   GREEN = '\033[92m'
   YELLOW = '\033[93m'
   RED = '\033[91m'
   BOLD = '\033[1m'
   UNDERLINE = '\033[4m'
   END = '\033[0m'


In [4]:
color.BOLD

'\x1b'

In [5]:
def rec_dd():
    return defaultdict(rec_dd)

In [6]:
system("taskset -p 0xff %d" % getpid())

0

In [7]:
strftime("%Y-%m-%d_%H%M%S", gmtime())

'2019-05-06_134438'

In [3]:
#Per leggere più strutture JSON presenti nello stesso documento
def decode_stacked(document, pos=0, decoder=JSONDecoder()):
    while True:
        match = NOT_WHITESPACE.search(document, pos)
        if not match:
            return
        pos = match.start()

        try:
            obj, pos = decoder.raw_decode(document, pos)
        except JSONDecodeError:
            # do something sensible if there's some error
            raise
        yield obj

In [4]:
# Passando il nome di un algoritmo, ottengo il suo id
def alg_id(alg_name):
    url = 'http://127.0.0.1:8081/api/algorithms'
    r = requests.get(url)
    resp_json = json.loads(r.content)
    for alg in resp_json:
        if alg_name in alg["fileName"]:
            return alg["id"]

In [5]:
alg_id("HyFD")

4

In [6]:
# Passando il nome di un algoritmo, ottengo il suo nome completo, incluso di estensione .jar
def alg_name_full(alg_name):
    url = 'http://127.0.0.1:8081/api/algorithms'
    r = requests.get(url)
    resp_json = json.loads(r.content)
    for alg in resp_json:
        if alg_name in alg["fileName"]:
            return alg["fileName"]

In [7]:
alg_name_full("HyFD")

u'HyFD-1.2-SNAPSHOT.jar'

In [8]:
# Passando il nome dell'algoritmo ottengo la lista di tutti i parametri necessari per eseguirlo
def requirements(alg_name):
    n = alg_name_full(alg_name) #nome completo da usare nella prossima API
    url = 'http://127.0.0.1:8081/api/parameter/' + n
    print url
    r = requests.get(url)
    resp_json = json.loads(r.content)
    for item in resp_json:
        del item["fixNumberOfSettings"]
    return resp_json
    

In [9]:
requirements("HyFD-1.2-SNAPSHOT.jar")

http://127.0.0.1:8081/api/parameter/HyFD-1.2-SNAPSHOT.jar


[{u'identifier': u'INPUT_GENERATOR',
  u'maxNumberOfSettings': 1,
  u'minNumberOfSettings': 1,
  u'numberOfSettings': 1,
  u'required': True,
  u'settings': None,
  u'type': u'ConfigurationRequirementRelationalInput'},
 {u'defaultValues': [True],
  u'identifier': u'NULL_EQUALS_NULL',
  u'maxNumberOfSettings': 1,
  u'minNumberOfSettings': 1,
  u'numberOfSettings': 1,
  u'required': True,
  u'settings': None,
  u'type': u'ConfigurationRequirementBoolean'},
 {u'defaultValues': [True],
  u'identifier': u'VALIDATE_PARALLEL',
  u'maxNumberOfSettings': 1,
  u'minNumberOfSettings': 1,
  u'numberOfSettings': 1,
  u'required': True,
  u'settings': None,
  u'type': u'ConfigurationRequirementBoolean'},
 {u'defaultValues': [True],
  u'identifier': u'ENABLE_MEMORY_GUARDIAN',
  u'maxNumberOfSettings': 1,
  u'minNumberOfSettings': 1,
  u'numberOfSettings': 1,
  u'required': True,
  u'settings': None,
  u'type': u'ConfigurationRequirementBoolean'},
 {u'defaultValues': [-1],
  u'identifier': u'MAX_DETER

In [10]:
# Passando il path di un ds ottengo le sue info,
# cioè quello che  deov mettere in settingsper il type:
# "ConfigurationRequirementRelationalInput"
def info_dataset(ds_path):
    url = 'http://127.0.0.1:8081/api/file-inputs'
    r = requests.get(url)
    resp_json = json.loads(r.content)
    for ds in resp_json:
        if ds_path == ds["name"]:
            ds["separatorChar"] = ds.pop("separator")
            ds["header"] = ds.pop("hasHeader")
            #print ds
            for item in ["name", "comment"]:
                del ds[item]
            ds["type"] = "ConfigurationSettingFileInput"
            return ds

In [11]:
info_dataset("/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_ARAMIS.csv")

{u'escapeChar': u'',
 u'fileName': u'/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_ARAMIS.csv',
 'header': True,
 u'id': 583,
 u'ignoreLeadingWhiteSpace': True,
 u'nullValue': u'',
 u'quoteChar': u'"',
 'separatorChar': u',',
 u'skipDifferingLines': False,
 u'skipLines': 0,
 u'strictQuotes': False,
 u'type': 'ConfigurationSettingFileInput'}

# OMNI

In [12]:
#Il body della richiesta
def omni(ds_path, result_name):
    print ds_path
    responses = []
    algs = {
        "SCDP": alg_id("SCDP"),
        "HyFD": alg_id("HyFD"),
        "HyUCC": alg_id("HyUCC"),
        "SPIDER": alg_id("SPIDER")
    }
    headers = {
        #"Host": "localhost:8081",
        "User-Agent": "Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:65.0) Gecko/20100101 Firefox/65.0",
        "Accept": "application/json, text/plain, */*",
        "Accept-Language": "it-IT,it;q=0.8,en-US;q=0.5,en;q=0.3",
        #"Accept-Encoding": "gzip, deflate",
        "Referer": "http://localhost:8080/",
        "Content-Type":"application/json;charset=utf-8",
        #"Content-Length": "1926",
        "Origin": "http://localhost:8080",
        "Connection": "keep-alive",
        "Pragma":"no-cache",
        "Cache-Control":"no-cache"
    }
    url = 'http://127.0.0.1:8081/api/algorithm-execution/'
    for alg in ["SCDP", "HyFD", "HyUCC", "SPIDER"]: #
        requirements_list = requirements(alg)
        #print "requirements_list"
        #print requirements_list
        for item in requirements_list:
            if item["type"] == "ConfigurationRequirementRelationalInput":
                #print "R.Input"
                #print "PRIMA"
                #print item
                #print "INFO_DATASET"
                #print info_dataset(ds_path)
                item["settings"] = [info_dataset(ds_path)]
                #print "DOPO"
                #print item
            else:
                item["settings"] = [{"type": item["type"].replace("Requirement","Setting"),
                                     "value": item["defaultValues"][0]}]
        body = {
            "algorithmId": algs[alg],
            "executionIdentifier": result_name + "_" + alg + strftime("%Y-%m-%d_%H%M%S", gmtime()),
            ##
            # Boh non capisco perché adesso devo mettere lower anche alg
            ##
            "requirements": requirements_list,
            "cacheResults":False,
            "writeResults":True,
            "countResults":False,
            "memory":""
        }
        #print json.dumps(body)
        r = requests.post(url, headers=headers, json=body)
        responses.append(json.loads(r.content))
    return responses 

# Questo esegue l'OMNI

In [22]:
# Se voglio processare solo alcuni file per ora sposto tutti gli indesiderati nella cartella "limbo"
# Poi penserò ad un modo più carino.
mypath = "/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/"
onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]
print onlyfiles
responses_list = []
for csv in onlyfiles:
    name = re.sub(r'.*_', '', csv)
    name = name.split(".")[0].lower()
    #print mypath + csv
    responses_list.append(omni(mypath + csv, name))

['organizations_Gerit.csv', 'organizations_P3.csv', 'organizations_Startup - Registro delle imprese.csv', 'organizations_Grid.csv', 'organizations_ARAMIS.csv', 'organizations_ORCID.csv', 'organizations_Consiglio Nazionale delle Ricerche (CNR).csv', 'organizations_Austrian Science Fund (FWF).csv', 'organizations_Arianna - Anagrafe Nazionale delle Ricerche.csv', 'organizations_Federal Office for the Environment - FOEN.csv', 'organizations_Questio.csv', 'organizations_Crawled.csv', 'organizations_Christian Doppler Forschungsgesellschaft.csv', 'organizations_SICRIS - Slovenian Current Research Informatio.csv', 'organizations_OpenAire.csv', 'organizations_ScanR.csv', 'organizations_CercaUniversita.csv', 'organizations_Patiris.csv']
/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_Gerit.csv
http://127.0.0.1:8081/api/parameter/SCDP-1.2-SNAPSHOT.jar
http://127.0.0.1:8081/api/parameter/HyFD-1.2-SNAPSHOT.jar
http://127.0.0.1:8081/api/parameter/HyUCC-1.2-SNAPSHOT.jar
http

In [23]:
# Classi per le varie dipendenze

class DEP(object):
    def __init__(self, lhs, rhs):
        if lhs == ['']:
            lhs = []
        self.lhs = lhs
        self.rhs = rhs
        
#     def __init__(self, x):
#         self.lhs = x.lhs
#         self.rhs = x.rhs
        
    def __hash__(self):
        return hash((tuple(self.lhs), tuple(self.rhs)))  # Passo dalle liste alle tuple per renderle hashabili
                                                         # Pare funzioni
    
    def __eq__(self, other):
        #print "uso eq!!!!1122333"
        return ((set(self.lhs), set(self.rhs)) == (set(other.lhs), set(other.rhs)))
        

#         return ((set(self.lhs), set(self.rhs)) == (set(other.lhs), set(other.rhs)) or
#                 (
#                   (set(self.lhs) <= set(other.lhs) and set(self.rhs) == set(other.rhs))
#                   or
#                   (set(other.lhs) <= set(slef.lhs) and set(self.rhs) == set(other.rhs))
#                 )
#                )
    def __le__(self, other): #Se self.lhs è un sottinsieme di other.rhs
        #print "uso le"
        return ((set(self.lhs) <= set(other.lhs)) and (set(self.rhs) == set(other.rhs)))
        
    def __ge__(self, other): #Se other.lhs è un sottinsieme di self.rhs
        #print "uso ge"
        return ((set(other.lhs) <= set(slef.lhs)) and (set(self.rhs) == set(other.rhs)))
        
    def __ne__(self, other):
        return not self.__eq__(other)

class FD(DEP):
    def __str__(self):
        return str(self.lhs) + " -> " + str(self.rhs) 
    
class IND(DEP):
    def __str__(self):
        return str(self.lhs) + " ⊆ " + str(self.rhs) 

class ORD(DEP):
    def __init__(self, lhs, rhs, order_type, comp):
        DEP.__init__(self, lhs, rhs)
        self.order_type = order_type
        self.comp = comp
    def __str__(self):
        return str(self.lhs) + " ~> " + str(self.rhs) + str(self.order_type) + str(self.comp)
    
class UCC(object): # UCC ha un solo attributo, quindi non lo faccio d erivare da DEP
    def __init__(self, comb):
        self.comb = comb
    def __hash__(self):
        return hash(tuple(self.comb))
    def __eq__(self, other):
        return set(self.comb) == set(other.comb)
    def __ne__(self, other):
        return not self.__eq__(other)
    def __str__(self):
        return str(self.comb)


In [24]:
# Pensiero di qualche funzione per rendere il codice più elegante, IN LAVORAZIONE
# PER ORA VA BENE COSì

# Lettura delle dipendenze

def create_dep(lhs, rhs, dep_type):
    if dep_type == "fds":
        return FD(lhs, rhs)
    elif dep_type == "inds":
        return IND(lhs, rhs)

def read_dep(file_name): # Il caso stats è a parte
    dep_type = re.sub(r'.*_', '', file_name)
    if dep_type == "uccs": # Caso UCC
        return read_uccs(file_name)
    columns = {}
    deps = []
    results = False
    f = open(file_name, "r")
    if dep_type == "fds": # Caso FD
        symbol = "->"
    elif dep_type == "inds": # Caso IND
        symbol = "[="
        
    for line in f:
        if line[0:2] == "1.":
            columns[line.split()[1]] = (line.split()[0][2:]) 
        elif line == "# RESULTS\n":
            results = True
        elif results == True:
            both = line.rstrip("\n").split(symbol)
            lhs = both[0].split(",") # Lo split mi crea una lista. Il problema è che l'ordine dei suoi elementi così conta, ma in verità un lhs [1,2] è uguale ad un [2,1]
            rhs = both[1].split(",")
            deps.append(create_dep(lhs, rhs, dep_type))
    return columns, deps

def read_stats(file_name):
    #with open('ris', 'r') as myfile:
    with open(file_name, 'r') as myfile:
        data=myfile.read().replace('\n', '')
    ris = pd.DataFrame()
    for obj in decode_stacked(data):
        tmp = pd.DataFrame.from_dict(obj["statisticMap"])
        tmp["columnIdentifier"] = obj["columnCombination"]["columnIdentifiers"][0]["columnIdentifier"]
        #print tmp
        #ris = ris.append(pd.DataFrame.from_dict(obj["statisticMap"]))
        ris = ris.append(tmp)
    ris = ris[ris.index == "value"]
    ris.index = ris["columnIdentifier"]
    return ris

def read_uccs(file_name):
    f = open(file_name, "r")
    columns = {}
    UCCs = []
    results = False
    for line in f:
        if line[0:2] == "1.":
            columns[(line.split()[0][2:])] = line.split()[1]
        elif line == "# RESULTS\n":
            results = True
        elif results == True:
            #print UCC(line.rstrip("\n").split(","))
            UCCs.append(UCC(line.rstrip("\n").split(",")))
            #print UCCs[0]
    return columns, UCCs

In [25]:
# Lista di tutti i file nella seguente cartella
mypath = "/home/marco/Scrivania/dep/results/"
onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]
onlyfiles

['orcid_SPIDER2019-05-17_144651_inds',
 'austrian science fund (fwf)_SPIDER2019-05-17_144729_inds',
 'startup - registro delle imprese_SPIDER2019-05-17_144600_inds',
 'consiglio nazionale delle ricerche (cnr)_HyFD2019-05-17_144711_fds',
 'orcid_HyUCC2019-05-17_144647_uccs',
 'openaire_SCDP2019-05-17_144908_stats',
 'sicris - slovenian current research informatio_SCDP2019-05-17_144851_stats',
 'p3_HyUCC2019-05-17_144540_uccs',
 'scanr_SPIDER2019-05-17_144949_inds',
 'aramis_SCDP2019-05-17_144622_stats',
 'patiris_SPIDER2019-05-17_145036_inds',
 'christian doppler forschungsgesellschaft_SCDP2019-05-17_144837_stats',
 'arianna - anagrafe nazionale delle ricerche_HyUCC2019-05-17_144740_uccs',
 'grid_HyUCC2019-05-17_144613_uccs',
 'crawled_HyFD2019-05-17_144824_fds',
 'austrian science fund (fwf)_HyUCC2019-05-17_144726_uccs',
 'cercauniversita_SCDP2019-05-17_145005_stats',
 'startup - registro delle imprese_HyFD2019-05-17_144553_fds',
 'christian doppler forschungsgesellschaft_HyFD2019-05-1

## Eseguo questo per leggere i file

In [26]:
#def read_all():
final_dep_results = defaultdict(dict)
stats = {}
attr_read = False
ds_names = []
for f in onlyfiles:
    #print f.split("_")[0]
    ds_name = f.split("_")[0] # invece di usare per es. orcid_SPIDER_inds,uso solo orcid
    ds_name = re.sub('[(){}<>]', '', ds_name) # Le parentesi non piacciono ai dict
    if "stats" not in f:
        attributes, dependencies = read_dep(mypath + f)
        if ds_name not in ds_names:
            ds_names.append(ds_name)
        #print f.split("_")
        dep_type = f.split("_")[-1] # idem per il tipo di dipendenza
        final_dep_results[ds_name][dep_type] =  dependencies
    else:
        #stats[f.split("_")[0]] = read_stats(mypath + f)
        #print mypath + f
        stats[ds_name] = read_stats(mypath + f)

In [22]:
a = dependencies[25]
b = dependencies[58]

In [23]:
print a

['1'] -> ['25']


In [24]:
print b

['23', '4', '12', '25'] -> ['33']


In [31]:
a = FD(['1', '3'], ['2'])
b = (['1'], ['2'])

In [32]:
a <= b

False

In [30]:
type(b.lhs[0])

str

In [48]:
attributes

{'1': 'id',
 '10': 'country',
 '11': 'countryCode',
 '12': 'postcode',
 '13': 'urbanUnit',
 '14': 'urbanUnitCode',
 '15': 'lat',
 '16': 'lon',
 '17': 'revenueRange',
 '18': 'privateFinanceDate',
 '19': 'employees',
 '2': 'acronyms',
 '20': 'typeCategoryCode',
 '21': 'typeLabel',
 '22': 'typeKind',
 '23': 'isPublic',
 '24': 'leaders',
 '25': 'staff',
 '26': 'links',
 '27': 'privateOrgTypeId',
 '28': 'privateOrgTypeLabel',
 '29': 'activities',
 '3': 'alias',
 '30': 'relations',
 '31': 'badges',
 '32': 'children',
 '33': 'identifiers',
 '4': 'label',
 '5': 'creationYear',
 '6': 'commercialLabel',
 '7': 'address',
 '8': 'city',
 '9': 'citycode'}

In [27]:
# Per le dipendenze MINIME COMUNI

def intersection_all(dep_type, dep_results):
    dep_intersection = []
    first = True
    for name in ds_names:
        dep_list = dep_results[name][dep_type]
        if first:           
            dep_intersection = set(dep_list).intersection(dep_list)
            first = False
        else:
            dep_intersection = set(dep_intersection).intersection(dep_list)
    return dep_intersection

# 1 Si crea la lista dei file presenti nella cartella
# 2 Si leggono questi file e si crea una lista con i loro nomi semplificati
# 3 Si calcola l'intersezione tra tutti loro su una certa dipendenza, es IND

In [28]:
# Per tutte le dipendenze comuni
# TODO: per ora funziona solo con le FDs. FATTO anche per INDs e UCCs
def intersezione_ign(a, b, dep_type):
    ris = []
    if dep_type == "fds":
        for i in a:
            #print i
            #print type(i)
            for j in b:
                #print 'Confronto {} e {}'.format(i, j)
                if i == j and i not in ris:
                    #print "buono ==, metto dentro {}".format(i)
                    ris.append(i)
                    #break  #Se un dataset ha []->7 e un altro ha [1]->7, [4]->7 e [31]->7,
                    #l'unico FD in comune segnalato è il primo [1]->7. Quindi tolgo il break
                elif i <= j and j not in ris:
                    #print "buono <=, metto dentro {}".format(j)
                    ris.append(j)
                    #break
                elif j <= i and i not in ris:
                    #print "buono >=, metto dentro {}".format(i)
                    ris.append(i)
                    #break
        
    elif dep_type == "inds" or dep_type == "uccs":
        for i in a:
            for j in b:
                #print 'Confronto {} e {}'.format(i, j)
                if i == j and i not in ris:
                    ris.append(i)
    return ris

In [29]:
def intersection_all_ign(dep_type, dep_results):
    dep_intersection = []
    first = True
    for name in ds_names:
        dep_list = dep_results[name][dep_type]
        if first:           
            dep_intersection = dep_list
            first = False
        else:
            dep_intersection = intersezione_ign(dep_intersection, dep_list, dep_type)
    return dep_intersection

def intersection_some_ign(dep_type, dep_results, datasets):
    dep_intersection = []
    first = True
    for name in datasets:
        print name
        dep_list = dep_results[name][dep_type]
        if first:           
            dep_intersection = dep_list
            first = False
        else:
            dep_intersection = intersezione_ign(dep_intersection, dep_list, dep_type)
    return dep_intersection



# 1 Si crea la lista dei file presenti nella cartella
# 2 Si leggono questi file e si crea una lista con i loro nomi semplificati
# 3 Si calcola l'intersezione tra tutti loro su una certa dipendenza, es IND

In [20]:
# Intersezioni MINIME COMUNI
inter_inds_min = intersection_all("inds", final_dep_results)
inter_fds_min = intersection_all("fds",final_dep_results)
inter_uccs_min = intersection_all("uccs", final_dep_results)

In [21]:
# Intersezioni COMUNI
inter_inds = intersection_all_ign("inds", final_dep_results)
inter_fds = intersection_all_ign("fds", final_dep_results)
inter_uccs = intersection_all_ign("uccs", final_dep_results)

In [23]:
ds_names

['alpsv20', 'alpsv20dedup']

In [22]:
# Lista di attributi nulli per un certo dataset

def find_null_attributes(name): # Restituisce lista con gli id degli attributi nulli
    null_attributes = []
    for index, row in stats[name].iterrows():
        #if row["Percentage of Distinct Values"] == 0:  # ATTENZIONE, da decidere, Number o Percentage?
        if row["Percentage of Nulls"] == 100:    
            null_attributes.append(row["columnIdentifier"])        
    return null_attributes

Escludo dall'intersezione le dipendenze con lhs nullo, dato che indicano colonne nulle. Le dipendenze ottenute sono poco significative.

ATTENZIONE, da esaminare bene questa cosa

In [25]:
# Per togliere le dipendenze nulle 
# TODO: per ora solo con le FDs
    # Messe anche le inds
    
    
# final_dep_results_no_null = defaultdict(dict)
# for dep_type in ["fds", "inds"]:
#     if dep_type == "fds":
#         for name in ds_names:
#             final_dep_results_no_null[name][dep_type] = [x for x in final_dep_results[name][dep_type] if x.lhs != []]
#     elif dep_type == "inds":
#         for name in ds_names:
#             null_attributes = find_null_attributes(name)
#             final_dep_results_no_null[name][dep_type] = [x for x in final_dep_results[name][dep_type] if x.lhs[0] not in null_attributes]

In [30]:
from copy import deepcopy
final_dep_results_copy = deepcopy(final_dep_results)

In [31]:
# Voglio escudere le dipendenze che considerano colonne vuote
# Adesso solo per le FD
# INUTILE, NON COMPAIONO MAI COME LHS, DEVO CONTTROLLARE IL RHS
# for name in ds_names:
#     print name
#     for i in final_dep_results[name]["fds"]:
#         print i
#         for el in i.lhs:
#             print el
#             print "Perc " + str(stats[name]["Percentage of Nulls"][attributes[el]])
#             print "-------"
#             if stats[name]["Percentage of Nulls"][attributes[el]] == 100:
#                 print i
#                 print "Ha {} nullo".format(el)
#                 final_dep_results[name]["fds"].remove(i)
#                 break

# Scrematura delle dipendenze, tolgo le nulle e quelle riconducibili ad una UCC (per lhs ho una UCC oppure un suo sovrainsieme)
for name in ds_names:
    print name
    for i in final_dep_results[name]["fds"]:
        #print i.rhs[0]
        #print "Perc " + str(stats[name]["Percentage of Nulls"][attributes[i.rhs[0]]])
        if stats[name]["Percentage of Nulls"][attributes[i.rhs[0]]] == 100:
            #print i
            #print "Ha {} nullo".format(i.rhs)
            final_dep_results_copy[name]["fds"].remove(i)  # Il remove creava dei problemi col for i, scombussolando l'ordine
            #print "-------"
        for j in final_dep_results[name]["uccs"]:
            if set(i.lhs) == set(j.comb) or set(i.lhs) >= set(j.comb):   #Trovo lo stesso caso mille volte ['1'] e ['1'], ['1'] e ['1'] eccc
                #print "lhs: {}, ucc: {}".format(i.lhs, j.comb)           #Penserò ad una soluzione
                #print "-------"
                final_dep_results_copy[name]["fds"].remove(i)
    
            

orcid
austrian science fund fwf
startup - registro delle imprese
consiglio nazionale delle ricerche cnr
p3
scanr
patiris
arianna - anagrafe nazionale delle ricerche
grid
crawled
christian doppler forschungsgesellschaft
questio
aramis
federal office for the environment - foen
sicris - slovenian current research informatio
cercauniversita
openaire
gerit


In [24]:
len(final_dep_results_copy["alpsv20dedup"]["fds"])

2261

In [32]:
dtypes_dict = {'id': int,
 'country': str,
 'countryCode': str,
 'postcode': str,
 'urbanUnit': str,
 'urbanUnitCode': str,
 'lat': float,
 'lon': float,
 'revenueRange': str,
 'privateFinanceDate': str,
 'employees': str,
 'acronyms': str,
 'typeCategoryCode': str,
 'typeLabel': str,
 'typeKind': str,
 'isPublic': str,
 'leaders': str,
 'staff': str,
 'links': str,
 'privateOrgTypeId': float,
 'privateOrgTypeLabel': str,
 'activities': str,
 'alias': str,
 'relations': str,
 'badges': str,
 'children': str,
 'identifiers': str,
 'label': str,
 'creationYear': str,
 'commercialLabel': str,
 'address': str,
 'city': str,
 'citycode': str}

In [26]:
#attributes

In [33]:
# opened_csvs contiene tutti i csv pronti per essere analizzati

opened_csvs = {}
csvpath = "/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/"
onlyfiles = [f for f in listdir(csvpath) if isfile(join(csvpath, f))]
for f in onlyfiles:
    only_name = re.sub(r'.*_', '', f).split('.')[0]
    only_name = re.sub('[(){}<>]', '', only_name)
    print only_name.lower()
    opened_csvs[only_name.lower()] = pd.read_csv('/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/' + f, sep=',', dtype=dtypes_dict)
#     for i in opened_csvs[only_name.lower()].columns:
#         print i
#         opened_csvs[only_name.lower()][i] = opened_csvs[only_name.lower()][i].astype(str)


gerit
p3
startup - registro delle imprese
grid
aramis
orcid
consiglio nazionale delle ricerche cnr
austrian science fund fwf
arianna - anagrafe nazionale delle ricerche
federal office for the environment - foen
questio
crawled
christian doppler forschungsgesellschaft
sicris - slovenian current research informatio
openaire
scanr
cercauniversita
patiris


In [69]:
# opened_csvs["scanr"]["id"] = opened_csvs["scanr"]["id"].astype(str)

In [70]:
# opened_csvs["scanr"].dtypes

In [34]:
for i in ds_names:
    opened_csvs[i] = opened_csvs[i].fillna(-1)
    
# Non una soluzione elegante, ma ogni tupla con almeno un elemento nullo non è considerata dal groupby
# e mi rende difficile testare le dipendenze

# Ricorda: le dipendenze considerano i valori null = null (come se avessero tutti lo stesso valore)
# quindi ['1', '2'] ->3 non è vero se ho tra le tuple:
#     1  2     3
#     a  null  x
#     a  null  y

In [29]:
#opened_csvs["aramis"]

In [30]:
# for name in opened_csvs.keys():
#     for i in opened_csvs[name].columns:
#         print i
#         opened_csvs[name][i] = opened_csvs[name][i].astype(str)


In [35]:
import difflib
import random
import requests
import ipywidgets as widgets

def multi_checkbox_widget(descriptions):
    """ Widget with a search field and lots of checkboxes """
    search_widget = widgets.Text()
    options_dict = {description: widgets.Checkbox(description=description, value=False) for description in descriptions}
    options = [options_dict[description] for description in descriptions]
    options_widget = widgets.VBox(options, layout={'overflow': 'scroll'})
    multi_select = widgets.VBox([search_widget, options_widget])

    # Wire the search field to the checkboxes
    def on_text_change(change):
        search_input = change['new']
        if search_input == '':
            # Reset search field
            new_options = [options_dict[description] for description in descriptions]
        else:
            # Filter by search field using difflib.
            close_matches = difflib.get_close_matches(search_input, descriptions, cutoff=0.0)
            new_options = [options_dict[description] for description in close_matches]
        options_widget.children = new_options

    search_widget.observe(on_text_change, names='value')
    return multi_select


In [36]:
data_sets = multi_checkbox_widget(ds_names)
data_sets

VkJveChjaGlsZHJlbj0oVGV4dCh2YWx1ZT11JycpLCBWQm94KGNoaWxkcmVuPShDaGVja2JveCh2YWx1ZT1GYWxzZSwgZGVzY3JpcHRpb249dSdvcmNpZCcpLCBDaGVja2JveCh2YWx1ZT1GYWzigKY=


In [37]:
selected_options = [widget.description for widget in data_sets.children[1].children if widget.value]

In [38]:
selected_options

[u'arianna - anagrafe nazionale delle ricerche', u'aramis']

In [39]:
# Intersezioni COMUNI solo su alcuni datasets
#inter_inds = intersection_some_ign("inds", final_dep_results, selected_options)
inter_fds = intersection_some_ign("fds", final_dep_results_copy, selected_options)
#inter_uccs = intersection_some_ign("uccs", final_dep_results, selected_options)

arianna - anagrafe nazionale delle ricerche
aramis


In [40]:
# Dipendenze esclusive per ogni dataset selezionato
exclusive_deps = defaultdict(dict)
for ds in selected_options:
    tmp = []
    for i in final_dep_results_copy[ds]["fds"]:
        if i not in inter_fds:
            p = False
            for y in inter_fds:
                if i <= y:
                    p = True
            if p == False:
                tmp.append(i)
    exclusive_deps[ds]["fds"] = tmp

In [57]:
len(exclusive_deps["arianna - anagrafe nazionale delle ricerche"]["fds"])

46

In [36]:
len(final_dep_results["alpsv20"]["fds"])
    

3243

In [37]:
len(final_dep_results_copy["alpsv20"]["fds"])
    

3184

In [38]:
len(final_dep_results["alpsv20dedup"]["fds"])

2333

In [39]:
len(final_dep_results_copy["alpsv20dedup"]["fds"])

2261

In [40]:
# A questo punto devo usare i csv e trovare le tuple che invalidano le dipendenze.
# es se ho i csv A e B dove A ha una dipendenza x che B non ha, vado ad analizzare le sue tuple e trovare le responsabili

In [41]:
# def bing_bing_bong(a_list, ds):    
#     eccez = []
#     for _, g in opened_csvs[ds].groupby([attributes[i] for i in a_list[:-1]]):
#         if len(g) > 1:
#             a = g[attributes[a_list[-1]]]
#             #print len(a.unique()) 
#             if len(a.unique()) != 1:
#                 eccez.append(a)
#     return eccez

def bing_bing_bong(a_list, ds):    
    eccez = []
    for _, g in opened_csvs[ds].groupby([attributes[i] for i in a_list[:-1]]):
        if len(g) > 1:
            g = g[attributes[a_list[-1]]]
            #print len(a.unique()) 
            if len(g.unique()) != 1:
#                 eccez.append(g)
                  eccez.append(g.unique())  # Così ho meno roba da salvare, vediamo se la situazione migliora
    return eccez

In [62]:
def bing_bing_bong(a_list, ds):    
    eccez = []
    
    for name, g in opened_csvs[ds].groupby([attributes[i] for i in a_list[:-1]]):
        start = time.time()
        if len(g) > 1:
            
            g = g[attributes[a_list[-1]]].unique()
            
            #print len(a.unique()) 
            if len(g) != 1:
                eccez.append(g)
        end = time.time()
        print (end-start)
#                   eccez.append(g.unique())  # Così ho meno roba da salvare, vediamo se la situazione migliora
    return eccez

In [44]:
a_list = ['2', '29', '32', '8', '4', '24', '26', '12', '25', '27']
a_list = ['7', '8', '4', '26', '13']
# start = time.time()
# e = bing_bing_bong(a_list, "alpsv20dedup")
# end = time.time()
# print (end - start)

In [50]:
# VECCHIO
def bing_bing_bong_new(a_list, ds):    
#     start = time.time()
    dict_df = opened_csvs[ds][[attributes[i] for i in a_list]].to_dict("split")
    dict_df_data = dict_df["data"]

    result = defaultdict(set)
    for row in dict_df_data:
        result[str(row[:-1])].add(row[-1])
    for key in result.keys():
        if len(result[key]) == 1:
            result.pop(key, None)
    return result
#     end = time.time()
#     print (end-start)

In [63]:
def bing_bing_bong_new(a_list, ds):    
#     start = time.time()
    dict_df = opened_csvs[ds][[attributes[i] for i in a_list]].to_dict("split")
    dict_df_data = dict_df["data"]

    result = defaultdict(lambda: defaultdict(int))

    for row in dict_df_data:
        result[str(row[:-1])][row[-1]] += 1
    for key in result.keys():
        if len(result[key]) == 1:
            result.pop(key, None)
    return result
#     end = time.time()
#     print (end-start)

In [78]:
# Se davvero funziona è almeno 10 volte più veloce
start = time.time()
# Trasformo il dataframe in un dict
dict_df = opened_csvs["alpsv20"][[attributes[i] for i in a_list]].to_dict("split")
dict_df_data = dict_df["data"]

# result = defaultdict(set)
result = defaultdict(lambda: defaultdict(int))

for row in dict_df_data:
#     result[str(row[:-1])].add(row[-1])
    result[str(row[:-1])][row[-1]] += 1

    # Se una chiave ha un un solo valore vuol dire che non genera una violazione, la tolgo
for key in result.keys():
    if len(result[key]) == 1:
        result.pop(key, None)
    
end = time.time()
print (end-start)

2.3535130024


In [79]:
result

defaultdict(<function __main__.<lambda>>,
            {"[-1, 'Orsay', 'Physique', -1]": defaultdict(int,
                         {-1: 1, '\xc3\x8ele-de-France': 1}),
             "[-1, 'Marseille', 'CPPM', -1]": defaultdict(int,
                         {-1: 1, "Provence Alpes Cote d'azur": 1}),
             "[-1, 'Messina', 'Economics', -1]": defaultdict(int,
                         {-1: 1, 'Sicily': 1}),
             "[-1, 'Bologna', 'Scienze Statistiche', -1]": defaultdict(int,
                         {-1: 3, 'Emilia-Romagna': 1}),
             "[-1, 'Lyon', 'Chemistry', -1]": defaultdict(int,
                         {-1: 1, 'Rh\xc3\xb4ne-Alpes': 3}),
             "[-1, 'Geneva', 'Molecular Biology', -1]": defaultdict(int,
                         {-1: 2, 'GE': 1}),
             "[-1, 'Siena', 'Department of Economics and Statistics', -1]": defaultdict(int,
                         {-1: 1, 'Toscana': 1}),
             "[-1, 'Bern', 'Division of Animal Welfare', -1]": defaultdict

In [43]:
# np.array([np.array(result.keys()), np.array(result.values())])

In [106]:
np.array([result.values()[0].keys(), result.values()[0].values()])

array([[ 74., 183.],
       [  1.,   1.]])

In [ ]:
np.array([np.array([1,2]), np.array(result.values())])

In [42]:
np.array([["a","b"], ["c", "d"]])

array([['a', 'b'],
       ['c', 'd']], dtype='|S1')

In [48]:
np.array([np.array([["a","b"], ["c", "d"]]), np.array([["e","f", "g"], ["h", "i", "j"]])])

ValueError: could not broadcast input array from shape (2,2) into shape (2)

In [134]:
np.array([1,2]), np.array(np.array(["a","b"], ["c", "d"]))

ciao


In [39]:
result

defaultdict(<function __main__.<lambda>>,
            {"[-1, 'Orsay', 'Physique', -1]": defaultdict(int,
                         {-1: 1, '\xc3\x8ele-de-France': 1}),
             "[-1, 'Marseille', 'CPPM', -1]": defaultdict(int,
                         {-1: 1, "Provence Alpes Cote d'azur": 1}),
             "[-1, 'Messina', 'Economics', -1]": defaultdict(int,
                         {-1: 1, 'Sicily': 1}),
             "[-1, 'Bologna', 'Scienze Statistiche', -1]": defaultdict(int,
                         {-1: 3, 'Emilia-Romagna': 1}),
             "[-1, 'Lyon', 'Chemistry', -1]": defaultdict(int,
                         {-1: 1, 'Rh\xc3\xb4ne-Alpes': 3}),
             "[-1, 'Geneva', 'Molecular Biology', -1]": defaultdict(int,
                         {-1: 2, 'GE': 1}),
             "[-1, 'Siena', 'Department of Economics and Statistics', -1]": defaultdict(int,
                         {-1: 1, 'Toscana': 1}),
             "[-1, 'Bern', 'Division of Animal Welfare', -1]": defaultdict

In [188]:
np.array([result.keys(), result.values()])[0]

array(["[-1, 'Zurich', 'Pharmacy', -1]", "[-1, 'Rouen', 'Marketing', -1]",
       "[-1, 'Graz', 'Archaeology', -1]",
       "[-1, 'Innsbruck', 'Institute of Botany', -1]",
       "[-1, 'Rome', 'Department of Computer, Control, and Management Engineering', -1]",
       "[-1, 'Magdeburg', 'River Ecology', -1]",
       "[-1, 'Torino', 'Dept. of Molecular Biotechnology and Health Sciences', -1]",
       "[-1, 'Trieste', 'DEAMS', -1]",
       "[-1, 'Zurich', 'Institute of Neuroinformatics', -1]",
       "[-1, 'Pavia', 'Department of Brain and Behavioral Sciences', -1]",
       "[-1, 'Vienna', 'Department of Crop Sciences', -1]",
       '[-1, "Villeneuve d\'Ascq", \'Physics\', -1]',
       "[-1, 'Brescia', 'Fisica', -1]",
       "[-1, 'Valbonne', 'Institut de Pharmacologie Mol\\xc3\\xa9culaire et Cellulaire', -1]",
       "[-1, 'Roma', 'PDTA', -1]", "[-1, 'Cagliari', 'Physics', -1]",
       "[-1, 'Stuttgart', 'Modern Magnetic Systems', -1]",
       "[-1, 'Pisa', 'Dipartimento di Matematica',

In [189]:
np.array([result.keys(), result.values()])[1]

array([defaultdict(<type 'int'>, {'ZH': 1, 'Zurich': 1}),
       defaultdict(<type 'int'>, {-1: 1, 'Normandy': 1}),
       defaultdict(<type 'int'>, {'Styria': 1, -1: 1}),
       defaultdict(<type 'int'>, {'Tirol': 1, -1: 1}),
       defaultdict(<type 'int'>, {'Lazio': 1, -1: 1}),
       defaultdict(<type 'int'>, {'Sachsen-Anhalt': 1, -1: 1}),
       defaultdict(<type 'int'>, {'Piemonte': 1, -1: 1}),
       defaultdict(<type 'int'>, {'Friuli-Venezia Giulia': 1, -1: 2}),
       defaultdict(<type 'int'>, {'ZH': 1, -1: 2}),
       defaultdict(<type 'int'>, {'Lombardia': 1, -1: 1}),
       defaultdict(<type 'int'>, {-1: 1, 'Vienna': 2}),
       defaultdict(<type 'int'>, {'Nord-Pas-de-Calais': 1, -1: 3}),
       defaultdict(<type 'int'>, {'Lombardia': 1, -1: 1}),
       defaultdict(<type 'int'>, {'PACA': 1, "C\xc3\xb4te d'Azur": 1}),
       defaultdict(<type 'int'>, {'Lazio': 4, 'Italia': 1}),
       defaultdict(<type 'int'>, {'Sardinia': 1, 'Sardegna': 2, -1: 1}),
       defaultdict(<type 

In [101]:
np.array(result.keys())

array(["[-1, 'Deggendorf', 'undefined', 'Deggendorf Institute of Technology', -1, -1, -1]",
       "[-1, 'ROVIGO', 'false', 'FLOID S.R.L.', 'https://www.floid.online/', -1, -1]",
       '[-1, \'GENOVA\', \'undefined\', "UNIVERSITA\' DEGLI STUDI DI GENOVA", -1, -1, -1]',
       "[-1, 'LA SPEZIA', 'false', 'HEALTHSPEZIA 24 UNIPERSONALE SRL', 'http://www.healthspezia24.it', -1, -1]",
       '[-1, \'FIRENZE\', \'undefined\', "UNIVERSITA\' DEGLI STUDI DI FIRENZE", -1, -1, -1]',
       "[-1, 'Bochum', 'undefined', 'Bochum University of Applied Sciences', 'https://www.hochschule-bochum.de/', -1, -1]",
       "[-1, 'Brescia', 'undefined', 'Department of economics and management', -1, -1, 'Niccol\\xc3\\xb2 Casnici']",
       "[-1, 'Trento', 'undefined', 'Museo delle Scienze', -1, -1, -1]",
       "[-1, 'Rome', 'undefined', 'John Cabot University', -1, -1, -1]",
       "[-1, 'BENEVENTO', 'false', 'INTELLIGENTIA S.R.L.', -1, -1, -1]",
       "[-1, 'SPADAFORA', 'false', 'VIVET GROUP SRL', -1, -1, 

In [112]:
asizeof([[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))])

11680

In [153]:
a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))]
a.append([])
a = np.array(a)
np.array([np.array(result.keys()), a])

In [154]:
a

array([list([[-1, 'Deggendorf'], [1, 1]]), list([['RO', -1], [1, 1]]),
       list([['Genova', -1], [1, 1]]), list([['SP', -1], [1, 1]]),
       list([['TOSCANA', 'Firenze'], [1, 1]]),
       list([['Bochum, Kreisfreie Stadt', 'Nordrhein-Westfalen'], [1, 1]]),
       list([['Lombardia', -1], [1, 1]]),
       list([['Trento', 'Trentino-Alto Adige'], [1, 1]]),
       list([['Lazio', 'Roma'], [1, 1]]),
       list([['BENEVENTO', 'BN'], [1, 1]]), list([['ME', -1], [1, 1]]),
       list([[-1, 'LI'], [1, 1]]), list([['Pavia', -1], [1, 1]]),
       list([['BA', -1], [1, 1]]),
       list([['M\xc3\xbcnchen, Landkreis', -1], [1, 1]]),
       list([['MODENA', 'MO'], [1, 1]]),
       list([['Trento', 'Trentino-Alto Adige'], [1, 1]]),
       list([['Rosenheim, Kreisfreie Stadt', 'Bayern'], [1, 1]]),
       list([[-1, 'TI'], [1, 1]]),
       list([['Slovenia', 'Savinjska'], [1, 1]]),
       list([['Schleswig-Holstein', 'Rendsburg-Eckernf\xc3\xb6rde'], [1, 1]]),
       list([['RM', -1], [1, 1]]), li

[[-1, 'Deggendorf'], [1, 1]]

In [116]:
A=np.array([[1,2],[],[1,2,3,4]])

In [117]:
A

array([list([1, 2]), list([]), list([1, 2, 3, 4])], dtype=object)

In [115]:
a = np.array([np.array(result.keys()), np.array([[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))])])
a
#                       np.array([np.array(result.keys()), np.array(result.values())])

TypeError: unhashable type: 'list'

In [99]:
np.array([np.array(result.keys()), np.array(result.values())])

array([["[-1, 'Deggendorf', 'undefined', 'Deggendorf Institute of Technology', -1, -1, -1]",
        "[-1, 'ROVIGO', 'false', 'FLOID S.R.L.', 'https://www.floid.online/', -1, -1]",
        '[-1, \'GENOVA\', \'undefined\', "UNIVERSITA\' DEGLI STUDI DI GENOVA", -1, -1, -1]',
        "[-1, 'LA SPEZIA', 'false', 'HEALTHSPEZIA 24 UNIPERSONALE SRL', 'http://www.healthspezia24.it', -1, -1]",
        '[-1, \'FIRENZE\', \'undefined\', "UNIVERSITA\' DEGLI STUDI DI FIRENZE", -1, -1, -1]',
        "[-1, 'Bochum', 'undefined', 'Bochum University of Applied Sciences', 'https://www.hochschule-bochum.de/', -1, -1]",
        "[-1, 'Brescia', 'undefined', 'Department of economics and management', -1, -1, 'Niccol\\xc3\\xb2 Casnici']",
        "[-1, 'Trento', 'undefined', 'Museo delle Scienze', -1, -1, -1]",
        "[-1, 'Rome', 'undefined', 'John Cabot University', -1, -1, -1]",
        "[-1, 'BENEVENTO', 'false', 'INTELLIGENTIA S.R.L.', -1, -1, -1]",
        "[-1, 'SPADAFORA', 'false', 'VIVET GROUP SRL

In [274]:
b = result.keys()[0:3]
b

["[-1, 'Zurich', 'Pharmacy', -1]",
 "[-1, 'Rouen', 'Marketing', -1]",
 "[-1, 'Graz', 'Archaeology', -1]"]

In [245]:
asizeof(a)

568

In [226]:
a = np.array([result.values()[0].keys(), result.values()[0].values()])

In [264]:
a= np.asarray(a)

In [260]:
asizeof(b)

384

In [263]:
b

array([[['ZH', 'Zurich'],
        ['1', '1']],

       [['-1', 'Normandy'],
        ['1', '1']],

       [['Styria', '-1'],
        ['1', '1']]], dtype='|S21')

In [279]:
np.array([np.array([result.keys()[0:3]]), np.array([np.array([result.values()[i].keys(), result.values()[i].values()]) for i in xrange(len(result))][0:3])])

ValueError: could not broadcast input array from shape (3,2,2) into shape (3)

In [294]:
a = np.array([np.array([[1,2,3]]), np.array([1,2], [1,2,3], [1,2,3,4]])])
asizeof(a)

112

In [299]:
a

array([array([[1, 2, 3]]),
       array([list([1, 2]), list([1, 2, 3]), list([1, 2, 3, 4])], dtype=object)],
      dtype=object)

In [293]:
a = np.array([np.array([1,2,3]), np.array([[1,2], [1,2,3], [1,2,3,4]])])
asizeof(a)

160

In [149]:
for i in xrange(len(result)):
    print i
    np.array([result.values()[i].keys(), result.values()[i].values()])

In [158]:
a = [1,2,3]
b = np.array(a)

In [148]:
[[i, i+1] for i in xrange(5)]

[[0, 1], [1, 2], [2, 3], [3, 4], [4, 5]]

In [123]:
result

defaultdict(<function __main__.<lambda>>,
            {"[-1, -1, -1, 'Ploemeur', 'AQUASTREAM', '56270', 'Non renseign\\xc3\\xa9', -1, 'Entreprise priv\\xc3\\xa9e', '56601']": defaultdict(int,
                         {74.0: 1, 183.0: 1})})

In [138]:
np.array([np.array(result.keys()), np.array([np.array([result.values()[i].keys(), result.values()[i].values()]) for i in xrange(len(result))])])

ValueError: could not broadcast input array from shape (2,2) into shape (2)

In [45]:
start = time.time()
# Scremo le dipendenze di ogni dataset sugli altri
# Su ds1 provo le dipendenze esclusive (che son state scremate) di ds2

# ATTENZIONE!!!!
# deps_screm = defaultdict(lambda: defaultdict(dict))
# scre_dict = defaultdict(lambda: defaultdict(dict)) #scremate, ma non testate. Quelle in dep_screm sono già state testate invece
# Con lambda non vanno come dovrebbero andare, non capisco
def rec_dd():
    return defaultdict(rec_dd)

# with open("porcazozza.txt", "w") as f:
deps_screm_nuovo = rec_dd()
# scre_dict = rec_dd()
for ds1 in selected_options:
    for ds2 in selected_options:
        if ds1 != ds2:
            tmp = []
            for i in exclusive_deps[ds2]["fds"][0:40]:
                print "controllo {} di {} su {}".format(i, ds2, ds1)
                if stats[ds1]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
                    new_i = deepcopy(i)
                    for x in i.lhs:
                        #print "esamino {}".format(x)
                        #print stats[ds1]["Percentage of Nulls"][attributes[x]]
                        #print "-----"
                        if stats[ds1]["Percentage of Nulls"][attributes[x]] == 100:
                            new_i.lhs.remove(x)
                    #print new_i
                    if new_i not in tmp:
                        tmp.append(new_i)

            #scre_dict[ds1][ds2] = tmp #à stesso discorso: provo su ds1 le dip esclusive di ds2,
                                      #ma queste sono scremate sulla struttura di ds1 
            #for dep in tmp:
                #print "ds1: {}, ds2: {}. Dep: {}".format(ds1, ds2, dep)
            for dep in tmp:
                #tmp_dict = {}
                #print dep
                #a_list = [el for el in dep.lhs]
                #print a_list
                a_list = dep.lhs
                #print a_list
                a_list.append(dep.rhs[0])
                #print "a_list: {}".format(a_list)
                if len(a_list) > 1:
                    #tmp_dict[str(a_list)] = bing_bing_bong(a_list, ds1)
                    #deps_screm[ds1][ds2]["fds"] = tmp_dict
                    result = bing_bing_bong_new(a_list, ds1)
                    if result:
                        # cioè se il dict non è vuoto (lo è se controllo delle "mezze" ucc) devo spiegarlo meglio questo discorso
#                     deps_screm_nuovo[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), np.array(result.values())])
#                         deps_screm_nuovo[ds1][ds2]["fds"][str(a_list)] = np.array([[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))])
#                         deps_screm_nuovo[ds1][ds2]["fds"][str(a_list)] = np.array([np.array([result.values()[i].keys(), result.values()[i].values()]) for i in xrange(len(result))])
                        a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))]
                        a.append([])
                        a = np.array(a)
                        deps_screm_nuovo[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), a])
                    else:
                        deps_screm_nuovo[ds1][ds2]["fds"][str(a_list)] = np.array([])
    
#                         f.write("%s\n" % bing_bing_bong(a_list, ds1))
end = time.time()
print(end-start)

controllo ['33'] -> ['2'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['24'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['9'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['5'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['13'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['17'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['3'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['14'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['27'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['28'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['19'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['30'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['18'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['21'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['20'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['10'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['11'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['22'] di alpsv20dedup su alpsv20
controllo ['33'] -> ['23'] di al

KeyboardInterrupt: 

In [160]:
deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"]["['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']"]

array([array(["[-1, -1, -1, -1, -1, 'false', 'PETALO S.R.L.', -1, -1, -1]",
       "[-1, -1, -1, -1, -1, 'undefined', 'neurology', -1, -1, 'didier smadja']",
       "[-1, -1, -1, -1, -1, 'undefined', 'Psychology', -1, -1, 'Tarek el Sehity']",
       "[-1, -1, -1, -1, -1, 'false', 'OPEN MIND S.R.L.', -1, -1, -1]",
       "[-1, -1, -1, -1, -1, 'undefined', 'Analytik', -1, -1, 'Fabian Ebert']"],
      dtype='|S74'),
       array([list([['CATANIA', 'MILANO'], [1, 1]]),
       list([['paris', 'Corbeil-Essonnes'], [1, 1]]),
       list([['Wien', 'Roma'], [1, 1]]),
       list([['MONTESARCHIO', 'TORINO'], [1, 1]]),
       list([['Wurzburg', 'W\xc3\xbcrzburg'], [1, 1]]), list([])],
      dtype=object)], dtype=object)

In [192]:
# Funzionante, ma lo sostituisco con la versione t_dict

# output = mp.Queue()

# def thread_function(lim1, lim2, lim1_d, lim2_d):
# #     scre_dict = rec_dd()
#     deps_screm_nuovo_process = rec_dd()
#     for ds1 in selected_options:
#             for ds2 in selected_options:
#                 if ds1 != ds2:
#                     tmp = []
#                     if ds2 == "alpsv20dedup":
#                         l1 = lim1_d
#                         l2 = lim2_d
#                     else:
#                         l1 = lim1
#                         l2 = lim2
#                     for i in exclusive_deps[ds2]["fds"][l1:l2]:
#                         #print "controllo {} di {} su {}".format(i, ds2, ds1)
#                         if stats[ds1]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
#                             new_i = deepcopy(i)
#                             for x in i.lhs:
#                                 #print "esamino {}".format(x)
#                                 #print stats[ds1]["Percentage of Nulls"][attributes[x]]
#                                 #print "-----"
#                                 if stats[ds1]["Percentage of Nulls"][attributes[x]] == 100:
#                                     new_i.lhs.remove(x)
#                             #print new_i
#                             if new_i not in tmp:
#                                 tmp.append(new_i)

#                     #scre_dict[ds1][ds2] = np.array(tmp, dtype=FD) #à stesso discorso: provo su ds1 le dip esclusive di ds2,
#                                               #ma queste sono scremate sulla struttura di ds1 
#                     #for dep in tmp:
#                         #print "ds1: {}, ds2: {}. Dep: {}".format(ds1, ds2, dep)
#                     for dep in tmp:
#                         #tmp_dict = {}
#                         #print dep
#                         #a_list = [el for el in dep.lhs]
#                         #print a_list
#                         a_list = dep.lhs
#                         #print a_list
#                         a_list.append(dep.rhs[0])
#                         #print "a_list: {}".format(a_list)
#                         if len(a_list) > 1:
#                             #tmp_dict[str(a_list)] = bing_bing_bong(a_list, ds1)
#                             #deps_screm[ds1][ds2]["fds"] = tmp_dict
#                             result = bing_bing_bong_new(a_list, ds1)
#                             if result:
#                                 a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))]
#                                 a.append([])
#                                 a = np.array(a)
#                                 deps_screm_nuovo_process[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), a])
#                             else:
#                                 deps_screm_nuovo_process[ds1][ds2]["fds"][str(a_list)] = np.array([])
#     print("Scrivo in output ds1: {}, ds2: {}".format(ds1, ds2))
#     output.put(deps_screm_nuovo_process)

In [69]:
import pymongo as pm
import pprint

In [88]:
client = pm.MongoClient()

In [83]:
client = "a"

In [89]:
db = client["Deps_db"]

In [90]:
fds_collection = db["FDS"]

In [80]:
fds_collection.drop()

In [91]:
for i in fds_collection.find():
    pprint.pprint(i)

{u'_id': ObjectId('5cded15032111fc70277d16b'),
 u'count': 2,
 u'dependencies': {u"['4', '12', '8']": [], u"['7', '4', '8']": []},
 u'source_ds': u'arianna - anagrafe nazionale delle ricerche',
 u'test_ds': u'aramis'}
{u'_id': ObjectId('5cded15032111fc70277d16c'),
 u'count': 1,
 u'dependencies': {u"['4', '8']": []},
 u'source_ds': u'arianna - anagrafe nazionale delle ricerche',
 u'test_ds': u'aramis'}


{u'_id': ObjectId('5cde7845f9dbf6d39bd30974'),
 u'count': 4,
 u'dependencies': {u'[10, 11]': [],
  u'[7, 8, 11]': [],
  u'[8, 10]': [],
  u'[8, 11]': []},
 u'source_ds': u'organizations_ARAMIS.csv',
 u'test_ds': u'organizations_Arianna - Anagrafe Nazionale delle Ricerche.csv'}

In [257]:
db.list_collection_names()

[]

In [68]:
fds_collection.estimated_document_count()

4

In [7]:
for i in fds_collection.find():
    pprint.pprint(i)

{u'_id': ObjectId('5cc5dbda52e08edbbac28fa8'),
 u'count': 1,
 u'dependencies': {u"['4', '12', '7']": [[u"['Sadepan Chimica S.R.L.', '46019']",
                                          u"['Cap S.p.A.', '16141']"],
                                         [[[u'V.le  Lombardia, 29',
                                            u'V.le Lombardia, 29'],
                                           [1, 1]],
                                          [[u'Lungobisagno Dalmazia, 71',
                                            u'Lungobisagno Dalmazia, 71/7'],
                                           [1, 1]]]]},
 u'source_ds': u'cercauniversita',
 u'test_ds': u'arianna - anagrafe nazionale delle ricerche'}
{u'_id': ObjectId('5cc5dbda52e08edbbac28fa9'),
 u'count': 1,
 u'dependencies': {u"['4', '12', '7']": [[u"['Sadepan Chimica S.R.L.', '46019']",
                                          u"['Cap S.p.A.', '16141']"],
                                         [[[u'V.le  Lombardia, 29',
              

In [78]:
mongo_dict = fds_collection.find_one({"source_ds": "aramis"})
type(mongo_dict)

NoneType

In [75]:
mongo_dict

{u'_id': ObjectId('5cdecd1032111fc70277d07a'),
 u'count': 2,
 u'dependencies': {u"['4', '12', '8']": [], u"['7', '4', '8']": []},
 u'source_ds': u'arianna - anagrafe nazionale delle ricerche',
 u'test_ds': u'aramis'}

In [ ]:
fds_collection.find

In [218]:
len(mongo_dict["dependencies"])

420

In [219]:
get_size(mongo_dict)

77300100

In [12]:
a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(mongo_dict["dependencies"]))]


NameError: name 'result' is not defined

In [146]:
for key in mongo_dict["dependencies"].keys():
    alias = mongo_dict["dependencies"][key]
    if alias:
        alias[1].append([])
        mongo_dict["dependencies"][key] = np.array([np.array(alias[0]), np.array(alias[1])])

In [144]:
get_size(mongo_dict) #list

16461660

In [147]:
get_size(mongo_dict) #array

29880196

In [149]:
mongo_dict

{u'_id': ObjectId('5cb6e5476a6d330ce11ab6e8'),
 u'dependencies': {u"['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']": array([array([u"[-1, -1, -1, -1, -1, 'false', 'PETALO S.R.L.', -1, -1, -1]",
         u"[-1, -1, -1, -1, -1, 'undefined', 'neurology', -1, -1, 'didier smadja']",
         u"[-1, -1, -1, -1, -1, 'undefined', 'Psychology', -1, -1, 'Tarek el Sehity']",
         u"[-1, -1, -1, -1, -1, 'false', 'OPEN MIND S.R.L.', -1, -1, -1]",
         u"[-1, -1, -1, -1, -1, 'undefined', 'Analytik', -1, -1, 'Fabian Ebert']"],
        dtype='<U74'),
         array([list([[u'CATANIA', u'MILANO'], [1, 1]]),
         list([[u'paris', u'Corbeil-Essonnes'], [1, 1]]),
         list([[u'Wien', u'Roma'], [1, 1]]),
         list([[u'MONTESARCHIO', u'TORINO'], [1, 1]]),
         list([[u'Wurzburg', u'W\xfcrzburg'], [1, 1]]), list([])],
        dtype=object)], dtype=object),
  u"['2', '8', '19', '4', '24', '26', '25', '13']": array([array([u"[-1, 'Dornbirn', -1, 'Fachhochschule Vorarlberg

In [138]:
key = "['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']"
key = "['7', '8', '11', '4', '26', '25']"

In [140]:
get_size(np.array(mongo_dict["dependencies"][key][0]))

5535968

In [139]:
get_size(mongo_dict["dependencies"][key][0])

1309368

In [143]:
mongo_dict["dependencies"][key][0]

[u"[-1, 'Strasbourg', 'FR', 'Chemistry', -1]",
 u"[-1, 'Munchen', 'DE', 'Division of Clinical Pharmacology', -1]",
 u"[-1, 'Marburg', 'DE', 'Faculty of Biology', -1]",
 u"[-1, 'Munchen', 'DE', 'Medizinische Fakult\\xc3\\xa4t', -1]",
 u"[-1, 'Trento', 'IT', 'Ingegneria Industriale', -1]",
 u"[-1, 'Potsdam', 'DE', 'Mathematics', -1]",
 u"[-1, 'Zurich', 'CH', 'Institute of Diagnostic and Interventional Radiology', -1]",
 u"[-1, 'Creteil', 'FR', 'Laboratoire Interuniversitaire des Syst\\xc3\\xa8mes Atmosph\\xc3\\xa9riques', -1]",
 u'[-1, \'Paris\', \'FR\', "Laboratoire d\'informatique de Paris 6", -1]',
 u"[-1, 'Vienna', 'AT', 'Institute of Science and Technology in Art', -1]",
 u"[-1, 'M\\xc3\\xbcnster', 'DE', 'Institute of Pharmaceutical Biology and Phytochemistry', -1]",
 u"[-1, 'Berlin', 'DE', 'Engineering', -1]",
 u"[-1, 'Pessac', 'FR', 'ENSEGID', -1]",
 u"[-1, 'Trento', 'IT', 'Industrial Engineering', -1]",
 u"[-1, 'Fisciano', 'IT', 'Dipartimento di Ingegneria Industriale', -1]",
 u"

In [67]:
sum_dict = defaultdict(int)

In [76]:
for key in mongo_dict["dependencies"].keys():
    somma = 0
#     print key
    if mongo_dict["dependencies"][key]:
        for i in mongo_dict["dependencies"][key][1]:
            somma += (sum(i[1]) - max(i[1]))
        sum_dict[key] = somma

In [77]:
sorted_x = sorted(sum_dict.items(), key=operator.itemgetter(1))
sorted_x

[]

In [66]:
def attributes_names(x):
    x = ast.literal_eval(x)
    names = []
    for i in x:
        names.append(attributes[i])
    return names

In [50]:
# for key in deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"].keys():
for key in sorted_x:
    print "Dependency: {}".format(key[0])
    print "Names: {}\n".format(attributes_names(key[0]))
    for i, j in zip(mongo_dict["dependencies"][key[0]][0], mongo_dict["dependencies"][key[0]][1]):
        print "\033[1m Key \033[0m: {}\n\033[1m Vals \033[0m: {}\n".format(i, j)
    print "----------------------"


Dependency: ['4', '12', '7']
Names: ['label', 'postcode', 'address']

 Key : ['Sadepan Chimica S.R.L.', '46019']
 Vals : [[u'V.le  Lombardia, 29', u'V.le Lombardia, 29'], [1, 1]]

 Key : ['Cap S.p.A.', '16141']
 Vals : [[u'Lungobisagno Dalmazia, 71', u'Lungobisagno Dalmazia, 71/7'], [1, 1]]

----------------------


In [101]:
get_size(a)

16461660

In [106]:
if a["dependencies"]["['33', '5']"]:
    print "full"
else:
    print "empty"

full


In [102]:
a["dependencies"]["['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']"]

[[u"[-1, -1, -1, -1, -1, 'false', 'PETALO S.R.L.', -1, -1, -1]",
  u"[-1, -1, -1, -1, -1, 'undefined', 'neurology', -1, -1, 'didier smadja']",
  u"[-1, -1, -1, -1, -1, 'undefined', 'Psychology', -1, -1, 'Tarek el Sehity']",
  u"[-1, -1, -1, -1, -1, 'false', 'OPEN MIND S.R.L.', -1, -1, -1]",
  u"[-1, -1, -1, -1, -1, 'undefined', 'Analytik', -1, -1, 'Fabian Ebert']"],
 [[[u'CATANIA', u'MILANO'], [1, 1]],
  [[u'paris', u'Corbeil-Essonnes'], [1, 1]],
  [[u'Wien', u'Roma'], [1, 1]],
  [[u'MONTESARCHIO', u'TORINO'], [1, 1]],
  [[u'Wurzburg', u'W\xfcrzburg'], [1, 1]]]]

In [94]:
for i in a["dependencies"]["['33', '5']"][1]:
    print i

IndexError: list index out of range

In [209]:
# # Versione t_dict
# # Mongodb non gestisce gli np.array, torno alle liste, ogni volta che ottengo i dati di una dipendenza li butto direttamente nel mio database
# # output = mp.Queue()

# def thread_function(lim1, lim2, lim1_d, lim2_d):
# #     scre_dict = rec_dd()
#     #deps_screm_nuovo_process = rec_dd()
#     client_p = pm.MongoClient()
#     db = client_p["Deps_db"]
#     fds_collection = db["FDS"]
#     seg_list = []
#     for ds1 in selected_options:
#             for ds2 in selected_options:
#                 if ds1 != ds2:
#                     tmp = []
#                     if ds2 == "alpsv20dedup":
#                         l1 = lim1_d
#                         l2 = lim2_d
#                     else:
#                         l1 = lim1
#                         l2 = lim2
#                     for i in exclusive_deps[ds2]["fds"][l1:l2]:
#                         #print "controllo {} di {} su {}".format(i, ds2, ds1)
#                         if stats[ds1]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
#                             new_i = deepcopy(i)
#                             for x in i.lhs:
#                                 #print "esamino {}".format(x)
#                                 #print stats[ds1]["Percentage of Nulls"][attributes[x]]
#                                 #print "-----"
#                                 if stats[ds1]["Percentage of Nulls"][attributes[x]] == 100:
#                                     new_i.lhs.remove(x)
#                             #print new_i
#                             if new_i not in tmp:
#                                 tmp.append(new_i)

#                     #scre_dict[ds1][ds2] = np.array(tmp, dtype=FD) #à stesso discorso: provo su ds1 le dip esclusive di ds2,
#                                               #ma queste sono scremate sulla struttura di ds1 
#                     #for dep in tmp:
#                         #print "ds1: {}, ds2: {}. Dep: {}".format(ds1, ds2, dep)
#                     t_dict = {
#                             "test_ds": ds1,
#                             "source_ds": ds2,
#                             "dependencies": {}
#                         }
# #                     print("t_dict: {}".format(t_dict))
#                     for dep in tmp:
#                         #tmp_dict = {}
#                         #print dep
#                         #a_list = [el for el in dep.lhs]
#                         #print a_list
#                         a_list = dep.lhs
#                         #print a_list
#                         a_list.append(dep.rhs[0])
#                         #print "a_list: {}".format(a_list)
#                         if len(a_list) > 1:
#                             #tmp_dict[str(a_list)] = bing_bing_bong(a_list, ds1)
#                             #deps_screm[ds1][ds2]["fds"] = tmp_dict
#                             result = bing_bing_bong_new(a_list, ds1)
#                             if result:
#                                 a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))]
# #                                 deps_screm_nuovo_process[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), a])
#                                 t_dict["dependencies"][str(a_list)] = [result.keys(), a]
#                             else:
#                                 t_dict["dependencies"][str(a_list)] = []
                    
# #                     print("t_dict: {}".format(t_dict))
# #                     print fds_collection.find_one({"test_ds": ds1, "source_ds": ds2})
#                     if not fds_collection.find_one({"test_ds": ds1, "source_ds": ds2}):
# #                         print "vuoto"
#                         fds_collection.insert_one(t_dict)
#                     else:
# #                         print "non vuoto"
#                         for k in t_dict["dependencies"].keys():
# #                             print("{} e' di tipo: {}".format(k, type(k)))
#                             t_dict["dependencies"]["dependencies."+k] = t_dict["dependencies"].pop(k)
# #                         print("t_dict mod: {}".format(t_dict))

#                         fds_collection.update_one({"test_ds": ds1, "source_ds": ds2}, {"$set": t_dict["dependencies"]})
# #     print("Scrivo in output ds1: {}, ds2: {}".format(ds1, ds2))
# #     output.put(deps_screm_nuovo_process)
# #     output.put(seg_list)

In [47]:
# Versione t_dict
# Mongodb non gestisce gli np.array, torno alle liste, ogni volta che ottengo i dati di una dipendenza li butto direttamente nel mio database
# output = mp.Queue()

# Altra versione, non quella base, provo a fare il bucketing dato che ho superato il limite dei 16 MB

def thread_function(lim1, lim2, lim1_d, lim2_d):
#     scre_dict = rec_dd()
    #deps_screm_nuovo_process = rec_dd()
    client_p = pm.MongoClient()
    db = client_p["Deps_db"]
    fds_collection = db["FDS"]
    seg_list = []
    for ds1 in selected_options:
            for ds2 in selected_options:
                if ds1 != ds2:
                    tmp = []
                    if ds2 == "alpsv20dedup":
                        l1 = lim1_d
                        l2 = lim2_d
                    else:
                        l1 = lim1
                        l2 = lim2
                    for i in exclusive_deps[ds2]["fds"][l1:l2]:
                        print "controllo {} di {} su {}".format(i, ds2, ds1)
                        if stats[ds1]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
                            new_i = deepcopy(i)
                            for x in i.lhs:
                                #print "esamino {}".format(x)
                                #print stats[ds1]["Percentage of Nulls"][attributes[x]]
                                #print "-----"
                                if stats[ds1]["Percentage of Nulls"][attributes[x]] == 100:
                                    new_i.lhs.remove(x)
                            #print new_i
                            if new_i not in tmp:
                                tmp.append(new_i)

                    #scre_dict[ds1][ds2] = np.array(tmp, dtype=FD) #à stesso discorso: provo su ds1 le dip esclusive di ds2,
                                              #ma queste sono scremate sulla struttura di ds1 
                    #for dep in tmp:
                        #print "ds1: {}, ds2: {}. Dep: {}".format(ds1, ds2, dep)
                    t_dict = {
                            "test_ds": ds1,
                            "source_ds": ds2,
                            "dependencies": {},
                            "count": 0
                        }
#                     print("t_dict: {}".format(t_dict))
                    for dep in tmp:
                        #tmp_dict = {}
                        #print dep
                        #a_list = [el for el in dep.lhs]
                        #print a_list
                        a_list = dep.lhs
                        #print a_list
                        a_list.append(dep.rhs[0])
                        #print "a_list: {}".format(a_list)
                        if len(a_list) > 1:
                            #tmp_dict[str(a_list)] = bing_bing_bong(a_list, ds1)
                            #deps_screm[ds1][ds2]["fds"] = tmp_dict
                            result = bing_bing_bong_new(a_list, ds1)
                            if result:
                                a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))]
#                                 deps_screm_nuovo_process[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), a])
                                t_dict["dependencies"][str(a_list)] = [result.keys(), a]
                            else:
                                t_dict["dependencies"][str(a_list)] = []
                    
                    for k in t_dict["dependencies"].keys():        
                        #t_dict["dependencies"]["dependencies."+k] = t_dict["dependencies"].pop(k) 
                        fds_collection.update_one(
                            {"test_ds": ds1, "source_ds": ds2, "count": {"$lt": 200}},
                            {
                                "$set": {"dependencies."+k: t_dict["dependencies"][k]},
                                "$inc": {"count": 1}
                            },
                            upsert=True
                        )
                
#                for i in xrange(3):
                    
#                     if not fds_collection.find_one({"test_ds": ds1, "source_ds": ds2, "count": {"$lt": 400-len(t_dict["dependencies)"])}}):
# #                         print "vuoto"
#                         fds_collection.insert_one(t_dict)
#                     else:
# #                         print "non vuoto"
#                         for k in t_dict["dependencies"].keys():
# #                             print("{} e' di tipo: {}".format(k, type(k)))
#                             t_dict["dependencies"]["dependencies."+k] = t_dict["dependencies"].pop(k)
# #                         print("t_dict mod: {}".format(t_dict))

#                         fds_collection.update_one({"test_ds": ds1, "source_ds": ds2}, {"$set": t_dict["dependencies"]})
#     print("Scrivo in output ds1: {}, ds2: {}".format(ds1, ds2))
#     output.put(deps_screm_nuovo_process)
#     output.put(seg_list)

In [82]:
## VERSIONE GENERALEEEEEEE


# Mongodb non gestisce gli np.array, torno alle liste, ogni volta che ottengo i dati di una dipendenza li butto direttamente nel mio database
# output = mp.Queue()

# Altra versione, non quella base, provo a fare il bucketing dato che ho superato il limite dei 16 MB

def process_function(sborat):
#     scre_dict = rec_dd()
    #deps_screm_nuovo_process = rec_dd()
    print sborat
    client_p = pm.MongoClient()
    db = client_p["Deps_db"]
    fds_collection = db["FDS"]
    seg_list = []
    for ds1 in selected_options:
            for ds2 in selected_options:
                if (ds1 != ds2 and sborat[ds2]):  # controllo se effettivamente ho delle dipendenze esclusive da controllare
                                                        # se infatti ne ho solo 2 lo split mi restituisce [0,0], [1,1], [], []
                                                        # gli ultimi due gruppi sono vuoti, quindi non faccio nulla con loro
                    tmp = []
#                     if ds2 == "alpsv20dedup":
#                         l1 = lim1_d
#                         l2 = lim2_d
#                     else:
#                         l1 = lim1
#                         l2 = lim2
                    l1 = sborat[ds2][0]
                    l2 = sborat[ds2][1]
                    for i in exclusive_deps[ds2]["fds"][l1:l2]:
                        #print "controllo {} di {} su {}".format(i, ds2, ds1)
                        if stats[ds1]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
                            new_i = deepcopy(i)
                            for x in i.lhs:
                                #print "esamino {}".format(x)
                                #print stats[ds1]["Percentage of Nulls"][attributes[x]]
                                #print "-----"
                                if stats[ds1]["Percentage of Nulls"][attributes[x]] == 100:
                                    new_i.lhs.remove(x)
                            #print new_i
                            if new_i not in tmp:
                                tmp.append(new_i)

                    #scre_dict[ds1][ds2] = np.array(tmp, dtype=FD) #à stesso discorso: provo su ds1 le dip esclusive di ds2,
                                              #ma queste sono scremate sulla struttura di ds1 
                    #for dep in tmp:
                        #print "ds1: {}, ds2: {}. Dep: {}".format(ds1, ds2, dep)
                    t_dict = {
                            "test_ds": ds1,
                            "source_ds": ds2,
                            "dependencies": {},
                            "count": 0
                        }
#                     print("t_dict: {}".format(t_dict))
                    for dep in tmp:
                        #tmp_dict = {}
                        #print dep
                        #a_list = [el for el in dep.lhs]
                        #print a_list
                        a_list = dep.lhs
                        #print a_list
                        a_list.append(dep.rhs[0])
                        #print "a_list: {}".format(a_list)
                        if len(a_list) > 1:
                            #tmp_dict[str(a_list)] = bing_bing_bong(a_list, ds1)
                            #deps_screm[ds1][ds2]["fds"] = tmp_dict
                            result = bing_bing_bong_new(a_list, ds1)
                            if result:
                                a = [[result.values()[i].keys(), result.values()[i].values()] for i in xrange(len(result))]
#                                 deps_screm_nuovo_process[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), a])
                                t_dict["dependencies"][str(a_list)] = [result.keys(), a]
                            else:
                                t_dict["dependencies"][str(a_list)] = []
                    
                    for k in t_dict["dependencies"].keys():        
                        #t_dict["dependencies"]["dependencies."+k] = t_dict["dependencies"].pop(k) 
                        fds_collection.update_one(
                            {"test_ds": ds1, "source_ds": ds2, "count": {"$lt": 200}},
                            {
                                "$set": {"dependencies."+k: t_dict["dependencies"][k]},
                                "$inc": {"count": 1}
                            },
                            upsert=True
                        )
                
#                for i in xrange(3):
                    
#                     if not fds_collection.find_one({"test_ds": ds1, "source_ds": ds2, "count": {"$lt": 400-len(t_dict["dependencies)"])}}):
# #                         print "vuoto"
#                         fds_collection.insert_one(t_dict)
#                     else:
# #                         print "non vuoto"
#                         for k in t_dict["dependencies"].keys():
# #                             print("{} e' di tipo: {}".format(k, type(k)))
#                             t_dict["dependencies"]["dependencies."+k] = t_dict["dependencies"].pop(k)
# #                         print("t_dict mod: {}".format(t_dict))

#                         fds_collection.update_one({"test_ds": ds1, "source_ds": ds2}, {"$set": t_dict["dependencies"]})
#     print("Scrivo in output ds1: {}, ds2: {}".format(ds1, ds2))
#     output.put(deps_screm_nuovo_process)
#     output.put(seg_list)

In [227]:
exclusive_deps["arianna - anagrafe nazionale delle ricerche"]["fds"][dict_process["aramis"][0]: dict_process["arianna - anagrafe nazionale delle ricerche"][1]]

In [59]:
def create_slides(n, n_slides):
    ris = [i for i in xrange(0, n, n_slides)]
    ris.append(n)
    return ris


def split(a, n):
    a = [i for i in xrange(a)]
    k, m = divmod(len(a), n)
    l = list(a[i * k + min(i, m):(i + 1) * k + min(i + 1, m)] for i in xrange(n))
    for i in xrange(len(l)):
        if l[i]:
            l[i] = [l[i][0], l[i][len(l[i])-1] +1]
    return l

ds_slides = {}
for ds in selected_options:
    # print ds
    if exclusive_deps[ds]:
        n = len(exclusive_deps[ds]["fds"])
    else:
        n = 0
    ds_slides[ds] = split(n, 4)

In [83]:
ds_slides

{u'aramis': [[], [], [], []],
 u'arianna - anagrafe nazionale delle ricerche': [[0, 12],
  [12, 24],
  [24, 35],
  [35, 46]]}

In [261]:
selected_options

[u'arianna - anagrafe nazionale delle ricerche', u'aramis', u'cercauniversita']

In [52]:
ds_slides = {}
for ds in ds_names:
    r = create_slides(len(exclusive_deps[ds]["fds"]), (len(exclusive_deps[ds]["fds"]) / 4) + 1)
    ds_slides[ds] = [[i,j] for i, j in zip(r[:-1], r[1:])]


KeyError: 'fds'

In [49]:
def split(a, n):
    a = [i for i in xrange(a)]
    k, m = divmod(len(a), n)
    l = list(a[i * k + min(i, m):(i + 1) * k + min(i + 1, m)] for i in xrange(n))
    for i in xrange(len(l)):
        if l[i]:
            l[i] = [l[i][0], l[i][len(l[i])-1] +1]
    return l

In [229]:
split(20, 4)

[[0, 5], [5, 10], [10, 15], [15, 20]]

In [230]:
ds_slide = {}
for ds in selected_options:
    print ds
    if exclusive_deps[ds]:
        n = len(exclusive_deps[ds]["fds"])
    else:
        n = 0
    ds_slides[ds] = split(n, 4)

arianna - anagrafe nazionale delle ricerche
aramis
cercauniversita


In [265]:
dict_process

{u'aramis': [],
 u'arianna - anagrafe nazionale delle ricerche': [36, 48],
 u'cercauniversita': [12, 15]}

In [221]:
dd = {}
for i in xrange(4):
    for ds in ds_slides.keys():
        dd[ds] = ds_slides[ds][i]  
    print dd


{u'arianna - anagrafe nazionale delle ricerche': [0, 11], u'aramis': [], u'cercauniversita': [0, 3]}
{u'arianna - anagrafe nazionale delle ricerche': [12, 23], u'aramis': [], u'cercauniversita': [4, 7]}
{u'arianna - anagrafe nazionale delle ricerche': [24, 35], u'aramis': [], u'cercauniversita': [8, 11]}
{u'arianna - anagrafe nazionale delle ricerche': [36, 47], u'aramis': [], u'cercauniversita': [12, 14]}


In [84]:
processes = []
dict_process = {}
l_d_p = []
# for i in xrange(len(slides)):
for i in xrange(4):
    for ds in ds_slides.keys():
        dict_process[ds] = ds_slides[ds][i]
    l_d_p.append(deepcopy(dict_process))
    #print l_d_p[i]
for i in l_d_p:
    print i
    processes.append(mp.Process(target=process_function, args=(i, )))

{u'arianna - anagrafe nazionale delle ricerche': [0, 12], u'aramis': []}
{u'arianna - anagrafe nazionale delle ricerche': [12, 24], u'aramis': []}
{u'arianna - anagrafe nazionale delle ricerche': [24, 35], u'aramis': []}
{u'arianna - anagrafe nazionale delle ricerche': [35, 46], u'aramis': []}


In [85]:
l_d_p

[{u'aramis': [], u'arianna - anagrafe nazionale delle ricerche': [0, 12]},
 {u'aramis': [], u'arianna - anagrafe nazionale delle ricerche': [12, 24]},
 {u'aramis': [], u'arianna - anagrafe nazionale delle ricerche': [24, 35]},
 {u'aramis': [], u'arianna - anagrafe nazionale delle ricerche': [35, 46]}]

In [86]:
start = time.time()
for x in processes:
    x.start()
# results = [output.get() for p in xrange(len(slides))]
for x in processes:
    x.join()
end = time.time()
print(end-start)

{u'arianna - anagrafe nazionale delle ricerche': [0, 12], u'aramis': []}
{u'arianna - anagrafe nazionale delle ricerche': [12, 24], u'aramis': []}
{u'arianna - anagrafe nazionale delle ricerche': [24, 35], u'aramis': []}
{u'arianna - anagrafe nazionale delle ricerche': [35, 46], u'aramis': []}
0.372954845428


In [143]:
t_dict = {"test_ds": "ds1",
          "source_ds": "ds2",
          "dependencies": {}
         }

In [146]:
t_dict["dependencies"]["ciao1"] = 2

In [147]:
t_dict

{'dependencies': {'ciao': 1, 'ciao1': 2}, 'source_ds': 'ds2', 'test_ds': 'ds1'}

In [47]:
for i in xrange(4):
    t_dict["fds"][i] = str(i)

In [92]:
fds_collection.find_one()

In [55]:
import threading
exitFlag = 0

class myThread (threading.Thread):
    def __init__(self, threadID, lim1, lim2):
        threading.Thread.__init__(self)
        self.threadID = threadID
        self.lim1 = lim1
        self.lim2 = lim2
    def run(self):
        print("Start {}, {}".format(self.threadID, time.time()))
        thread_function(self.lim1, self.lim2)
        print("End {}, {}".format(self.threadID, time.time()))

# def print_time(threadName, counter, delay):
#     while counter:
#         if exitFlag:
#             threadName.exit()
#             time.sleep(delay)
#             print "%s: %s" % (threadName, time.ctime(time.time()))
#             counter -= 1

In [51]:
def create_slides(n, n_slides):
    ris = [i for i in xrange(0, n, n_slides)]
#     ris.append(n)
    return ris

In [126]:
n = 6
r = create_slides(n, (n/4)+1)
print r
slides_d = [[i,j] for i, j in zip(r[:], r[1:])]
if len(slides_d) < 4:
    slides_d.append([n-1, n-1])
print slides_d

[0, 2, 4]
[[0, 2], [2, 4], [5, 5]]


In [129]:
[i for i in xrange(20)]

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19]

In [170]:
l = [[1,2], []]

In [171]:
min(2, l[1])

2

In [177]:
a = 3

In [178]:
split(a, 4)

[[0, 0], [1, 1], [2, 2], []]


In [158]:
l = split(a,4)
for i inn l:
    if len(i) 

[[0], [1], [2], [3]]

In [71]:
r = create_slides(len(exclusive_deps["alpsv20dedup"]["fds"]), (len(exclusive_deps["alpsv20dedup"]["fds"]) / 4) + 1)
slides_d = [[i,j] for i, j in zip(r[:-1], r[1:])]
len(slides_d)
#     print("{}:{}".format(i,j))

4

In [72]:
slides_d

[[0, 212], [212, 424], [424, 636], [636, 844]]

In [73]:
r = create_slides(len(exclusive_deps["alpsv20"]["fds"]), (len(exclusive_deps["alpsv20"]["fds"]) / 4) + 1)
slides = [[i,j] for i, j in zip(r[:-1], r[1:])]
len(slides)

4

In [103]:
def incr(a):
    a += 1
a = 3
incr(a)
print a

3


In [74]:
slides

[[0, 365], [365, 730], [730, 1095], [1095, 1457]]

In [34]:
for i in  xrange(0, 40-1, 10-1):
    print i

0
9
18
27
36


In [35]:
r = create_slides(40, 10)
slides = [[i,j] for i, j in zip(r[:-1], r[1:])]
slides_d = [[i,j] for i, j in zip(r[:-1], r[1:])]
len(slides)

4

In [36]:
r

[0, 10, 20, 30, 40]

In [37]:
slides

[[0, 10], [10, 20], [20, 30], [30, 40]]

In [38]:
slides_d

[[0, 10], [10, 20], [20, 30], [30, 40]]

In [78]:
threads = []
for i in xrange(len(slides)):
#     print "{}, {}".format(slides[i][0], slides[i][1])
    threads.append(myThread(i, slides[i][0], slides[i][1]))

NameError: name 'myThread' is not defined

In [76]:
len(processes)

4

Process Process-5:
Traceback (most recent call last):
  File "/home/marco/anaconda2/lib/python2.7/multiprocessing/process.py", line 267, in _bootstrap
    self.run()
  File "/home/marco/anaconda2/lib/python2.7/multiprocessing/process.py", line 114, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-70-082258dc0251>", line 77, in thread_function
    upsert=True
  File "/home/marco/anaconda2/lib/python2.7/site-packages/pymongo/collection.py", line 995, in update_one
    session=session),
  File "/home/marco/anaconda2/lib/python2.7/site-packages/pymongo/collection.py", line 851, in _update_retryable
    _update, session)
  File "/home/marco/anaconda2/lib/python2.7/site-packages/pymongo/mongo_client.py", line 1248, in _retryable_write
    return self._retry_with_session(retryable, func, s, None)
  File "/home/marco/anaconda2/lib/python2.7/site-packages/pymongo/mongo_client.py", line 1201, in _retry_with_session
    return func(session, sock_info, retryable)
  File 

1809.05910897


In [158]:
t_dict

{'dependencies': {'ciao': 1, 'ciao1': 2}, 'source_ds': 'ds2', 'test_ds': 'ds1'}

In [84]:
# results[3]

In [63]:
p = mp.Process(target=thread_function, args=(0, 5))
p1 = mp.Process(target=thread_function, args=(5, 10))
p1 = mp.Process(target=thread_function, args=(10, 15))

p.start()
p1.start()

p.join()
p1.join()

In [87]:
def dict_merge(dct, merge_dct):
    """ Recursive dict merge. Inspired by :meth:``dict.update()``, instead of
    updating only top-level keys, dict_merge recurses down into dicts nested
    to an arbitrary depth, updating keys. The ``merge_dct`` is merged into
    ``dct``.
    :param dct: dict onto which the merge is executed
    :param merge_dct: dct merged into dct
    :return: None
    """
    for k, v in merge_dct.iteritems():
        if (k in dct and isinstance(dct[k], dict)
                and isinstance(merge_dct[k], collections.Mapping)):
            dict_merge(dct[k], merge_dct[k])
        else:
            dct[k] = merge_dct[k]

In [186]:
import collections

In [187]:
tot = rec_dd()

In [199]:
# Funzionante, ma lo sostituisco con la versione t_dict
# for i in results:
#     dict_merge(tot, i)

In [89]:
for col in xrange(len(results[0])):
    tot = rec_dd()
    for row in results:
        dict_merge(tot, row[col])
    fds_collection.insert_one(tot)

InvalidDocument: Cannot encode object: array([], dtype=float64)

In [203]:
with open("pickle.txt", "w") as f:
    pickle.dump(tot, f)

In [204]:
with open("pickle.txt", "r") as f:
    tot_loaded = pickle.load(f)

In [222]:
bbbbb = rec_dd()
type(bbbbb)

collections.defaultdict

In [220]:
type(tot_loaded)

collections.defaultdict

In [214]:
tot["alpsv20"]["alpsv20dedup0"]["fds"]["['10', '19', '4', '24', '26', '12', '5']"]
    

defaultdict(<function __main__.rec_dd>, {})

In [244]:
sum_dict = defaultdict(int)

In [245]:
for key in tot_loaded["alpsv20dedup"]["alpsv20"]["fds"].keys():
    somma = 0
    for i in tot_loaded["alpsv20dedup"]["alpsv20"]["fds"][key][1]:
        if i:
            somma += (sum(i[1]) - max(i[1]))
    sum_dict[key] = somma

In [85]:
# sum_dict

In [86]:
# tot_loaded["alpsv20"]["alpsv20dedup"]["fds"].keys()

In [99]:
len(bb["alpsv20dedup"]["alpsv20"]["fds"])

12

In [56]:
start = time.time()
for i in processes:
    i.start()
for x in processes:
    x.join()
end = time.time()
print(end-start)

894.437335968


In [57]:
#with open("porcazozza.txt", "w") as f:
deps_screm_nuovo1 = rec_dd()
scre_dict = rec_dd()
for ds1 in [selected_options[0]]:
        for ds2 in [selected_options[1]]:
            if ds1 != ds2:
                tmp = []
                for i in exclusive_deps[ds2]["fds"][0:40]:
                    if stats[ds1]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
                        new_i = deepcopy(i)
                        for x in i.lhs:
                            #print "esamino {}".format(x)
                            #print stats[ds1]["Percentage of Nulls"][attributes[x]]
                            #print "-----"
                            if stats[ds1]["Percentage of Nulls"][attributes[x]] == 100:
                                new_i.lhs.remove(x)
                        #print new_i
                        if new_i not in tmp:
                            tmp.append(new_i)

                #scre_dict[ds1][ds2] = np.array(tmp, dtype=FD) #à stesso discorso: provo su ds1 le dip esclusive di ds2,
                                          #ma queste sono scremate sulla struttura di ds1 
                #for dep in tmp:
                    #print "ds1: {}, ds2: {}. Dep: {}".format(ds1, ds2, dep)
                for dep in tmp:
                    #tmp_dict = {}
                    #print dep
                    #a_list = [el for el in dep.lhs]
                    #print a_list
                    a_list = dep.lhs
                    #print a_list
                    a_list.append(dep.rhs[0])
                    #print "a_list: {}".format(a_list)
                    if len(a_list) > 1:
                        #tmp_dict[str(a_list)] = bing_bing_bong(a_list, ds1)
                        #deps_screm[ds1][ds2]["fds"] = tmp_dict
                        result = bing_bing_bong_new(a_list, ds1)
                        deps_screm_nuovo1[ds1][ds2]["fds"][str(a_list)] = np.array([np.array(result.keys()), np.array(result.values())])
                        #f.write("%s\n" % bing_bing_bong(a_list, ds1))

In [70]:
with open('p.txt', 'r') as f:
    s = f.read()
    #dict_read = ast.literal_eval(s)

In [87]:
# deps_screm_nuovo1

In [83]:
asizeof(result.keys())

4232

In [85]:
asizeof(np.array(result.keys()))

3944

In [73]:
a = (np.array(result.values()))

In [77]:
asizeof(a)

368

In [56]:
np.array([np.array(result.keys()), np.array(result.values())])[1]

array([set(['TE', -1]), set(['MI', -1]), set(['SA', -1]), set(['VE', -1]),
       set(['PV', -1])], dtype=object)

In [300]:
# print s

In [43]:
from __future__ import print_function
# print deps_screm_nuovo
# print("Hello stackoverflow!", file=open("output.txt", "a"))
with open("Output_tot_no_mt.txt", "w") as text_file:
    print(deps_screm_nuovo, file=text_file)
#     text_file.write("{0}".format(deps_screm_nuovo))
#str_d = "{}".format(deps_screm_nuovo)



In [81]:
with open("Output_mt.txt", "w") as text_file:
    print(deps_screm_nuovo, file=text_file)

In [301]:
# print(d)

In [318]:
# Questo!!!!!

for key in copia_dict["alpsv20"]["alpsv20dedup"]["fds"].keys():
    #print(key)
    copia_dict["alpsv20"]["alpsv20dedup"]["fds"][key][1] = [list(i) for i in copia_dict["alpsv20"]["alpsv20dedup"]["fds"][key][1]]
    copia_dict["alpsv20"]["alpsv20dedup"]["fds"][key] = copia_dict["alpsv20"]["alpsv20dedup"]["fds"][key].tolist()
        

In [315]:
[list(i) for i in copia_dict["alpsv20"]["alpsv20dedup"]["fds"]["['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']"][1]]

[['CATANIA', 'MILANO'],
 ['paris', 'Corbeil-Essonnes'],
 ['Wien', 'Roma'],
 ['MONTESARCHIO', 'TORINO'],
 ['Wurzburg', 'W\xc3\xbcrzburg']]

In [311]:
for i in copia_dict["alpsv20"]["alpsv20dedup"]["fds"]["['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']"][1]:
    i = list(i)

In [322]:
copia_dict["alpsv20"]["alpsv20dedup"]["fds"]["['2', '7', '32', '9', '19', '23', '4', '26', '12', '25', '8']"]

[["[-1, -1, -1, -1, -1, 'false', 'PETALO S.R.L.', -1, -1, -1]",
  "[-1, -1, -1, -1, -1, 'undefined', 'neurology', -1, -1, 'didier smadja']",
  "[-1, -1, -1, -1, -1, 'undefined', 'Psychology', -1, -1, 'Tarek el Sehity']",
  "[-1, -1, -1, -1, -1, 'false', 'OPEN MIND S.R.L.', -1, -1, -1]",
  "[-1, -1, -1, -1, -1, 'undefined', 'Analytik', -1, -1, 'Fabian Ebert']"],
 [['CATANIA', 'MILANO'],
  ['paris', 'Corbeil-Essonnes'],
  ['Wien', 'Roma'],
  ['MONTESARCHIO', 'TORINO'],
  ['Wurzburg', 'W\xc3\xbcrzburg']]]

In [313]:
a = [1,2]
for i in a:
    i=i+1

[1, 2]

In [278]:
asizeof(copia_dict)

284040

In [88]:
# json.dumps(copia_dict)

In [253]:
a = np.array([["[-1, 'IT', 'PETALO S.R.L.', -1]",
        "[-1, 'FR', 'Hospices Civils de Lyon', 'http://www.chu-lyon.fr/fr/web']",
        "['VIA CUMA 28', 'IT', 'PRIUS SISTEMA INTEGRATO DIAGNOSI E TERAPIA S.R.L.', -1]",
        "['VIA SELICE 84/A', 'IT', 'REMEMBRANE SRL', 'http://remembrane.com/']",
        "[-1, 'FR', 'Institut National de Recherches Arch\\xc3\\xa9ologiques Pr\\xc3\\xa9ventives', 'https://www.inrap.fr/']",
        "[-1, 'IT', 'OPEN MIND S.R.L.', -1]",
        "[-1, 'IT', 'Ospedale San Paolo', 'http://www.ao-sanpaolo.it/']",
        "[-1, 'DE', 'Hochschulbibliothekszentrum des Landes Nordrhein-Westfalen', 'https://www.hbz-nrw.de/']",
        "['VIA FONDAZZA 53', 'IT', 'CELLPLY SRL', 'https://www.cellply.com/']",
        "[-1, 'FR', 'Universit\\xc3\\xa9 Lille 2 Droit et Sant\\xc3\\xa9', 'https://www.univ-lille.fr']",
        "['VIA SPEZIA 20', 'IT', 'HPF NUTRACEUTICS S.R.L.', -1]",
        "[-1, 'CH', 'Schweizer Kompetenzzentrum Sozialwissenschaften', 'https://forscenter.ch/en/']",
        "['VIA SVIZZERA 16', 'IT', 'AB ANALITICA SRL', 'http://www.abanalitica.com']",
        '[\'VIA PONTE DON MELILLO\', \'IT\', "PRODAL SCARL SOCIETA\' CONSORTILE A RESPONSABILITA\' LIMITATA", -1]',
        '["VIA LOCALITA\' COSTE SANT\'AGOSTINO", \'IT\', \'CONSORZIO UNIVERSITARIO PER GLI STUDI ECONOMICI E FINANZIARI - CO SEF\', -1]',
        "[-1, 'DE', 'Leibniz Institute of Freshwater Ecology and Inland Fisheries', 'https://www.igb-berlin.de/']",
        "[-1, 'FR', 'Fondation pour la Recherche M\\xc3\\xa9dicale', 'https://www.frm.org/']",
        "['VIA DELLA REPUBBLICA 51', 'IT', 'BIOESPLORA SRL', 'http://www.bioesplora.it']",
        "['VIA DEGLI ARTIGIANI 27', 'IT', 'BRIGHT SOLUTIONS S.R.L.', 'http://brightsolutions.it/']",
        "[-1, 'DE', 'Leibniz Institute for Applied Geophysics', 'https://www.leibniz-liag.de/en/home.html']"],
       [set(['Thu Aug 14 00:00:00 CEST 2014', 'Fri Oct 02 00:00:00 CEST 2015']),
        set(['Fri Jan 01 00:00:00 CET 1802', -1]),
        set(['Fri Oct 26 00:00:00 CEST 2007', -1]),
        set(['Wed Sep 29 00:00:00 CEST 2010', -1]),
        set(['Mon Jan 01 00:00:00 CET 2001', -1]),
        set(['Thu May 10 00:00:00 CEST 2018', 'Tue May 31 00:00:00 CEST 2016']),
        set([-1, 'Thu Jan 01 00:00:00 CET 1987']),
        set(['Mon Jan 01 00:00:00 CET 1962', -1]),
        set(['Wed Dec 18 00:00:00 CET 2013', -1]),
        set(['Sun Jan 01 00:00:00 CET 1559', -1]),
        set(['Fri Jun 29 00:00:00 CEST 2007', -1]),
        set(['Tue Jan 01 00:00:00 CET 2008', -1]),
        set([-1, 'Fri Mar 23 00:00:00 CET 1990']),
        set(['Thu May 18 00:00:00 CEST 2006', -1]),
        set([-1, 'Wed Apr 29 00:00:00 CEST 2009']),
        set(['Wed Jan 01 00:00:00 CET 1992', -1]),
        set(['Wed Jan 01 00:00:00 CET 1947', -1]),
        set(['Fri Feb 27 00:00:00 CET 2009', -1]),
        set(['Tue Mar 10 00:00:00 CET 1998', -1]),
        set(['Sat Jan 01 00:00:00 CET 2000', -1])]], dtype=object)

array([["[-1, 'IT', 'PETALO S.R.L.', -1]",
        "[-1, 'FR', 'Hospices Civils de Lyon', 'http://www.chu-lyon.fr/fr/web']",
        "['VIA CUMA 28', 'IT', 'PRIUS SISTEMA INTEGRATO DIAGNOSI E TERAPIA S.R.L.', -1]",
        "['VIA SELICE 84/A', 'IT', 'REMEMBRANE SRL', 'http://remembrane.com/']",
        "[-1, 'FR', 'Institut National de Recherches Arch\\xc3\\xa9ologiques Pr\\xc3\\xa9ventives', 'https://www.inrap.fr/']",
        "[-1, 'IT', 'OPEN MIND S.R.L.', -1]",
        "[-1, 'IT', 'Ospedale San Paolo', 'http://www.ao-sanpaolo.it/']",
        "[-1, 'DE', 'Hochschulbibliothekszentrum des Landes Nordrhein-Westfalen', 'https://www.hbz-nrw.de/']",
        "['VIA FONDAZZA 53', 'IT', 'CELLPLY SRL', 'https://www.cellply.com/']",
        "[-1, 'FR', 'Universit\\xc3\\xa9 Lille 2 Droit et Sant\\xc3\\xa9', 'https://www.univ-lille.fr']",
        "['VIA SPEZIA 20', 'IT', 'HPF NUTRACEUTICS S.R.L.', -1]",
        "[-1, 'CH', 'Schweizer Kompetenzzentrum Sozialwissenschaften', 'https://forscenter.ch/

In [247]:
copia_dict["alpsv20"]["alpsv20dedup"]["fds"][key].size

0

In [246]:
key

"['33', '11']"

In [169]:
copia_dict = re.sub('<[^>]+>,', '', copia_dict)

In [170]:
# copia_dict = re.sub('array\\(.*?4\\)\\, ', '', copia_dict)

In [229]:
copia_dict = re.sub(re.escape("array([], shape=(2, 0), dtype=float64)"), 'array([])', copia_dict)

In [233]:
copia_dict = dict(copia_dict)

ValueError: dictionary update sequence element #0 has length 1; 2 is required

In [236]:
json.dumps(deps)

TypeError: array([], shape=(2, 0), dtype=float64) is not JSON serializable

In [166]:
# copia_dict = re.sub("defaultdict", "", copia_dict)

In [89]:
# print(copia_dict)

In [183]:
a = defaultdict(
    {u'alpsv20': defaultdict(
        {u'alpsv20dedup': defaultdict(
            {'fds': defaultdict(
                {"['7', '11', '4', '26', '5']": np.array([
                    "[-1, 'IT', 'PETALO S.R.L.', -1]",
                    "[-1, 'FR', 'Hospices Civils de Lyon', 'http://www.chu-lyon.fr/fr/web']"
                ])
                })})})})
                

TypeError: first argument must be callable or None

In [204]:
json.dumps(deps_screm_nuovo, open("ciao.txt", "w"))

TypeError: array([], shape=(2, 0), dtype=float64) is not JSON serializable

In [215]:
core_data_type = lambda: [0] * 10
test = rec_dd()
test['hello']['world']['example'][5] = 100
print(test)
print(json.dumps(test))

defaultdict(<function rec_dd at 0x7fec666e6f50>, {'hello': defaultdict(<function rec_dd at 0x7fec666e6f50>, {'world': defaultdict(<function rec_dd at 0x7fec666e6f50>, {'example': defaultdict(<function rec_dd at 0x7fec666e6f50>, {5: 100})})})})
{"hello": {"world": {"example": {"5": 100}}}}


In [217]:
print(json.dumps(deps_screm_nuovo))

TypeError: array([], shape=(2, 0), dtype=float64) is not JSON serializable

In [211]:
class NestedDefaultDict(defaultdict):
    def __init__(self, depth, default=int, _root=True):
        self.root = _root
        self.depth = depth
        if depth > 1:
            cur_default = lambda: NestedDefaultDict(depth - 1,
                                                    default,
                                                    False)
        else:
            cur_default = default
        defaultdict.__init__(self, cur_default)

    def __repr__(self):
        if self.root:
            return "NestedDefaultDict(%d): {%s}" % (self.depth,
                                                    defaultdict.__repr__(self))
        else:
            return defaultdict.__repr__(self)

In [212]:
core_data_type = lambda: [0] * 10
test = NestedDefaultDict(3, core_data_type)
test['hello']['world']['example'][5] += 100
print test
print json.dumps(test)

SyntaxError: invalid syntax (<ipython-input-212-daa536261514>, line 4)

In [181]:
a = {'fds': defaultdict(
                {"['33', '5']": "['7', '11', '4', '26', '5']": np.array([[
                    "[-1, 'IT', 'PETALO S.R.L.', -1]",
                    "[-1, 'FR', 'Hospices Civils de Lyon', 'http://www.chu-lyon.fr/fr/web']"
                ]])})}

SyntaxError: invalid syntax (<ipython-input-181-ae148d0eefc5>, line 2)

In [75]:
a = {'alpsv20':
 {'alpsv20dedup':
  {'fds':
   {"['33', '5']": np.array([], shape=(2, 0), dtype=float64), "['7', '11', '4', '26', '5']": np.array([["[-1, 'IT', 'PETALO S.R.L.', -1]", "[-1, 'FR', 'Hospices Civils de Lyon', 'http://www.chu-lyon.fr/fr/web']"]])
   }
  }
 }
}

NameError: name 'float64' is not defined

In [87]:
deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"]

defaultdict(<function __main__.rec_dd>,
            {"['2', '32', '8', '4', '24', '26', '12', '25', '27']": array([['[-1, -1, \'CAGLIARI\', "CONSORZIO BIOTECNO-MARES (CONSORZIO NAZIONALE ITALIANO DELLE BIOT ECNOLOGIE, DELLE METODOLOGIE DELL\'ACQUACOLTURA E DELLA RICERCA ECOCOMPATIBILE E SOSTENIBILE)", -1, -1, \'09124\', -1]',
                     '[-1, -1, \'VITERBO\', "G.A.I.A. - GESTIONE AMBIENTALE INTEGRATA ED ACQUACOLTURA (SERVIZI PER L\'AMBIENTE E LA PESCA) SOCIETA\' COOPERATIVA", -1, -1, \'01100\', -1]'],
                    [set([125.0, 6.0]), set([65.0, 150.0])]], dtype=object),
             "['2', '32', '8', '4', '24', '26', '12', '25', '28']": array([['[-1, -1, \'CAGLIARI\', "CONSORZIO BIOTECNO-MARES (CONSORZIO NAZIONALE ITALIANO DELLE BIOT ECNOLOGIE, DELLE METODOLOGIE DELL\'ACQUACOLTURA E DELLA RICERCA ECOCOMPATIBILE E SOSTENIBILE)", -1, -1, \'09124\', -1]',
                     '[-1, -1, \'VITERBO\', "G.A.I.A. - GESTIONE AMBIENTALE INTEGRATA ED ACQUACOLTURA (SERVIZI PER L\'

In [67]:
deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"]["['2', '32', '8', '4', '24', '26', '12', '25', '27']"][1]

array([set([125.0, 6.0]), set([65.0, 150.0])], dtype=object)

In [69]:
for i, j in zip(deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"]["['2', '32', '8', '4', '24', '26', '12', '25', '27']"][0], deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"]["['2', '32', '8', '4', '24', '26', '12', '25', '27']"][1]):
    print i
    print j
    print "x"

[-1, -1, 'CAGLIARI', "CONSORZIO BIOTECNO-MARES (CONSORZIO NAZIONALE ITALIANO DELLE BIOT ECNOLOGIE, DELLE METODOLOGIE DELL'ACQUACOLTURA E DELLA RICERCA ECOCOMPATIBILE E SOSTENIBILE)", -1, -1, '09124', -1]
set([125.0, 6.0])
x
[-1, -1, 'VITERBO', "G.A.I.A. - GESTIONE AMBIENTALE INTEGRATA ED ACQUACOLTURA (SERVIZI PER L'AMBIENTE E LA PESCA) SOCIETA' COOPERATIVA", -1, -1, '01100', -1]
set([65.0, 150.0])
x


In [90]:
# for key in deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"].keys():
#     print "Dependency: {}".format(key)
#     for i, j in zip(deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"][key][0], deps_screm_nuovo["alpsv20dedup"]["alpsv20"]["fds"][key][1]):
#         print "\033[1m Key \033[0m: {}\n\033[1m Vals \033[0m: {}\n".format(i, j)


In [259]:
asizeof(deps_screm)

472210536

In [91]:
asizeof(deps_screm_nuovo)

8677368

In [64]:
with open("p.txt", "w") as f:
    f.write("%s\n" % deps_screm_nuovo)

In [234]:
deps_screm["alpsv20"]["alpsv20dedup"]["fds"].keys() == deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"].keys()

True

In [91]:
# for i in deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"]:
#     print i
#     print deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"][i][0]
#     print "I\nI\nI"
#     print deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"][i][1]
#     print "--------------------------------------------"

In [215]:
for i in xrange(100):
    if "VIA LOCALIT" in deps_screm["alpsv20"]["alpsv20dedup"]["fds"]["['7', '10', '4', '26', '27']"][0][i]:
        print i

58


IndexError: index 67 is out of bounds for axis 0 with size 67

NameError: name 'sys' is not defined

In [92]:
# deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"]["['7', '8', '10', '4', '26', '25']"][1]

In [252]:
len(deps_screm["alpsv20"]["alpsv20dedup"]["fds"]["['7', '8', '10', '4', '26', '25']"])

4724

In [241]:
deps_screm_nuovo["alpsv20"]["alpsv20dedup"]["fds"]["['7', '10', '4', '26', '27']"][:, 58]

array(['["VIA LOCALITA\' COSTE SANT\'AGOSTINO", \'Italy\', \'CONSORZIO UNIVERSITARIO PER GLI STUDI ECONOMICI E FINANZIARI - CO SEF\', -1]',
       set([160.0, 176.0])], dtype=object)

In [93]:
# deps_screm["alpsv20"]["alpsv20dedup"]["fds"]

In [94]:
# for i in deps_screm["alpsv20"]["alpsv20dedup"]["fds"]:
#     print deps_screm["alpsv20"]["alpsv20dedup"]["fds"][i]
#     print "I\nI\nI"
#     print deps_screm["alpsv20"]["alpsv20dedup"]["fds"][i][1]
#     print "--------------------------------------------"

In [95]:
# deps_screm

In [96]:
# scre_dict["alpsv20"]["alpsv20dedup"]

In [139]:
for i in scre_dict["alpsv20"]["alpsv20dedup"]:
    print i

TypeError: 'builtin_function_or_method' object is not iterable

In [128]:
# len(scre_dict["alpsv20"]["alpsv20dedup"])
for i in scre_dict["alpsv20"]["alpsv20dedup"]:
    print i

TypeError: 'builtin_function_or_method' object is not iterable

In [109]:
len(scre_dict["alpsv20dedup"]["alpsv20"])

1087

In [148]:
asizeof(scre_dict)

16688

In [149]:
asizeof(scre_dict["alpsv20"]["alpsv20dedup"])

6848

In [150]:
asizeof(scre_dict["alpsv20dedup"]["alpsv20"])

8792

1475352

In [51]:
import sys
#deps_screm["alpsv20"]["alpsv20dedup"]["fds"].keys()

In [60]:
len(exclusive_deps["alpsv20"]["fds"])

1457

In [39]:
len(scre_dict["alpsv20dedup"]["alpsv20"])

1087

In [41]:
len(exclusive_deps["alpsv20dedup"]["fds"])

844

In [42]:
len(scre_dict["alpsv20"]["alpsv20dedup"])

844

In [65]:
print "0: {}".format(selected_options[0])
print "1: {}".format(selected_options[1])
# Su 0 provo le dipendenze di 1
#deps_screm[selected_options[0]][selected_options[1]]["fds"].keys()

0: alpsv20
1: alpsv20dedup


In [118]:
deps_screm[selected_options[1]][selected_options[0]]["fds"].keys()

KeyError: 'fds'

In [149]:
def deps_out(a, b):
    for dep in deps_screm[a][b]["fds"].keys():
        l = ast.literal_eval(dep)
        print "{} -> {}".format(l[:-1], l[-1])
        # a = [attributes[i] for i in l[:-1]]
        print "{} -> ['{}']".format(str([attributes[i] for i in l[:-1]]), str(attributes[l[-1]]))
        print "\n"

        for i in deps_screm[a][b]["fds"][dep]:
            print opened_csvs["scanr"][[attributes[j] for j in l[:-1]]].iloc[i.index[0]]
            print i.to_string()
            print "------------------------------------------------------"
        print "xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx\n \
               xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx "


In [97]:
# deps_out(selected_options[0], selected_options[1])  

In [117]:
deps_out(selected_options[1], selected_options[0])

KeyError: 'fds'

In [57]:
a_list = ['city', 'links', 'postcode']
b = opened_csvs["scanr"][['id', 'city', 'links', 'postcode']].loc[[9615, 25328]]
b

id    city links postcode
9615   223916  Acigné    -1    35690
25328  239629  Acigné    -1    35690

In [63]:
b["postcode"].iloc[0]

'35690'

In [64]:
b["postcode"].iloc[1]

'35690'

In [124]:
opened_csvs["scanr"][[attributes[i] for i in l]].iloc[0]

city              Feuquières-en-Vimeu
links       https://www.decayeux.com/
postcode                        80210
Name: 0, dtype: object

In [84]:
deps_screm["scanr"]["sicris - slovenian current research information system"]["fds"].keys()

["['7', '8', '28', '26']",
 "['26', '12', '8']",
 "['7', '12']",
 "['7', '8', '27', '26']",
 "['7', '26', '27']",
 "['8', '26', '12']",
 "['7', '26', '28']"]

In [79]:
print s.index

Index([u'a', u'b', u'c', u'd', u'e'], dtype='object')


In [98]:
# for i in deps_screm["scanr"]["sicris - slovenian current research information system"]["fds"]["['7', '12']"]:
#     print i

In [99]:
# deps_screm["scanr"]["sicris - slovenian current research information system"]["fds"]["['7', '12']"]

In [67]:
attributes["12"]

'postcode'

In [60]:
for i in deps_screm["sicris - slovenian current research information system"]["scanr"]["fds"]["['4', '32']"]:
    print i
    print "-------------------------------------------------------------------------- \n"

KeyError: "['4', '32']"

In [56]:
a_list = ['2', '7', '8', '26', '12']
a = bing_bing_bong(a_list)
for i in a:
    print i

NameError: global name 'prova' is not defined

In [ ]:
for i in 

In [67]:
klk = ['1','2']
k = defaultdict(dict)

In [68]:
k[str(klk)] = 3

In [69]:
k

defaultdict(dict, {"['1', '2']": 3})

In [81]:
# Dipendenze esclusive di startup

for i in final_dep_results_copy["startup - registro delle imprese"]["fds"]:
    if i not in inter_fds:
        p = False
        for y in inter_fds:
            if i <= y:
                p = True
        if p == False:
            print i

[] -> ['22']
['4', '26'] -> ['21']
['8', '4'] -> ['13']
['8', '4'] -> ['27']
['8', '4'] -> ['28']
['8', '4'] -> ['21']
['29', '4'] -> ['21']
['4', '13'] -> ['8']
['4', '13'] -> ['27']
['4', '13'] -> ['28']
['4', '13'] -> ['21']
['29', '8', '5', '26'] -> ['27']
['29', '8', '5', '26'] -> ['28']
['29', '5', '26'] -> ['21']
['29', '5', '26', '13'] -> ['27']
['29', '5', '26', '13'] -> ['28']
['8', '5'] -> ['13']
['29', '8'] -> ['13']


In [82]:
# Dipendenze esclusive di grid

con = []
for i in final_dep_results_copy["grid"]["fds"]:
    if i not in inter_fds:
        p = False
        for y in inter_fds:
            if i <= y:
                p = True
        if p == False:
            print i
            con.append(i)

['4'] -> ['12']
['4'] -> ['7']
['4', '26'] -> ['2']
['3', '4', '26'] -> ['5']
['4', '13'] -> ['2']
['4', '13'] -> ['3']
['4', '13'] -> ['32']
['4', '13'] -> ['5']
['5', '4'] -> ['3']
['10', '5', '4'] -> ['2']
['11', '5', '4'] -> ['2']
['26'] -> ['12']
['26'] -> ['7']
['32', '9', '5', '26', '27'] -> ['2']
['32', '9', '5', '26', '28'] -> ['2']
['32', '8', '5', '26', '27'] -> ['2']
['32', '8', '5', '26', '28'] -> ['2']
['32', '5', '26', '27', '13'] -> ['2']
['32', '5', '26', '28', '13'] -> ['2']
['2'] -> ['12']
['2'] -> ['7']
['9'] -> ['13']
['32', '9', '5'] -> ['12']
['7', '9', '5'] -> ['12']
['32', '8', '5'] -> ['12']
['7', '8', '5'] -> ['12']
['32', '5', '13'] -> ['12']
['7', '5', '13'] -> ['12']
['32'] -> ['7']
['12'] -> ['7']


In [83]:
# Scremo le dipendenze grid su starup
con_screm = []
for i in con:
    if stats["startup - registro delle imprese"]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
        good = True
        new_i = deepcopy(i)
        for x in i.lhs:
            print "esamino {}".format(x)
            print stats["startup - registro delle imprese"]["Percentage of Nulls"][attributes[x]]
            print "-----"
            if stats["startup - registro delle imprese"]["Percentage of Nulls"][attributes[x]] == 100:
                new_i.lhs.remove(x)
        
        print new_i
        if new_i not in con_screm:
            con_screm.append(new_i)

esamino 3
100
-----
esamino 4
0
-----
esamino 26
21
-----
['4', '26'] -> ['5']
esamino 4
0
-----
esamino 13
0
-----
['4', '13'] -> ['5']
esamino 9
100
-----
[] -> ['13']


In [84]:
for i in con_screm:
    print i

['4', '26'] -> ['5']
['4', '13'] -> ['5']
[] -> ['13']


In [80]:
# Dipendenze esclusive di startup

con = []
for i in final_dep_results_copy["startup - registro delle imprese"]["fds"]:
    if i not in inter_fds:
        p = False
        for y in inter_fds:
            if i <= y:
                p = True
        if p == False:
            print i
            con.append(i)

[] -> ['22']
['4', '26'] -> ['21']
['8', '4'] -> ['13']
['8', '4'] -> ['27']
['8', '4'] -> ['28']
['8', '4'] -> ['21']
['29', '4'] -> ['21']
['4', '13'] -> ['8']
['4', '13'] -> ['27']
['4', '13'] -> ['28']
['4', '13'] -> ['21']
['29', '8', '5', '26'] -> ['27']
['29', '8', '5', '26'] -> ['28']
['29', '5', '26'] -> ['21']
['29', '5', '26', '13'] -> ['27']
['29', '5', '26', '13'] -> ['28']
['8', '5'] -> ['13']
['29', '8'] -> ['13']


In [100]:
# # Scremo le dipendenze startup su grid
# con_screm = []
# for i in con:
#     if stats["grid"]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
#         good = True
#         new_i = deepcopy(i)
#         for x in i.lhs:
#             print "esamino {}".format(x)
#             print stats["grid"]["Percentage of Nulls"][attributes[x]]
#             print "-----"
#             if stats["grid"]["Percentage of Nulls"][attributes[x]] == 100:
#                 new_i.lhs.remove(x)
        
#         print new_i
#         if new_i not in con_screm:
#             con_screm.append(new_i)

In [52]:
for i in con_screm:
    print i

['8', '4'] -> ['13']
['8', '4'] -> ['27']
['8', '4'] -> ['28']
['4', '13'] -> ['8']
['4', '13'] -> ['27']
['4', '13'] -> ['28']
['8', '5', '26'] -> ['27']
['8', '5', '26'] -> ['28']
['5', '26', '13'] -> ['27']
['5', '26', '13'] -> ['28']
['8', '5'] -> ['13']
['8'] -> ['13']


In [195]:
# A questo punto devo aprire i csv e trovare le tuple che invalidano le dipendenze.
# es se ho i csv A e B dove A ha una dipendenza x che B non ha, vado ad analizzare le sue tuple e trovare le responsabili
prova = pd.read_csv('/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_Startup - Registro delle imprese.csv', sep=',')

In [187]:
a_list = ['4', '26', '5']
a = bing_bing_bong(a_list)
for i in a:
    print i

In [104]:
for i in final_dep_results["startup - registro delle imprese"]["fds"]:
    if i.rhs[0] == '5':
        print i

['1'] -> ['5']
['33'] -> ['5']
['8', '4', '26'] -> ['5']
['29', '4', '26'] -> ['5']
['4', '26', '13'] -> ['5']
['29', '8', '4'] -> ['5']
['29', '4', '13'] -> ['5']


In [20]:
attributes

NameError: name 'attributes' is not defined

In [150]:
# Con la trovata dei null, ma soprattutto delle UCC le dipendenze trovate sono moooolto di meno, bene

# for i in inter_fds:
#     print i

In [149]:
# Le dipepndenze trovate sono molte, se considerassi solo quelle con pochi elementi nel LHS?
# for i in inter_fds:
#     if len(i.lhs) == 1:
#         print i

In [178]:
# for i in final_dep_results_copy["openaire"]["fds"]:
#     if i not in inter_fds:
#         print i


# Questo dovrebbe andare bene, non devo solamente controllare che un elemento sia nell'intersezione,
# devo anche controllare se l'elemento analizzato è un sottinsieme di un memebro dell'intersezione
# es se ['1', '4'] -> ['7'] non c'è nell'intersezione, ma però c'è ['1', '4', '10'] -> ['7']
# allora è come se ci fosse e facesse parte dll'intersezione.
# Se invece non è nemmeno sottinsieme di nessuno, allora vuol dire che non compare proprio in nessuna forma nell'intersezione
# C'è viceversa da considerare se è un sovrainsieme? Non credo proprio, perché stiamo gestendo dipendenze minime, e tra due dipendenze viene presa la più grande (specifica)
# Considerando lo stesso es di prima 1, 4 è un sottinsieme di 1,4,10
# Mentre 1,4,10 massimo può essere sé stesso (spiegazione piuttosto brutta, ma credo si capisca)

# Dipendenze esclusive di openaire
for i in final_dep_results_copy["openaire"]["fds"]:
    if i not in inter_fds:
        p = False
        for y in inter_fds:
            if i <= y:
                p = True
        if p == False:
            print i

['2', '7', '4', '26'] -> ['12']
['7', '4'] -> ['10']
['7', '4'] -> ['11']
['4', '12'] -> ['10']
['4', '12'] -> ['11']
['8', '4'] -> ['10']
['8', '4'] -> ['11']
['2', '7', '26'] -> ['8']


In [26]:
# for i in final_dep_results_copy["openaire"]["fds"]:
#     if i not in inter_fds:
#         print "Mezzo"
#         print i
#         p = False
#         for y in inter_fds:
#             if i <= y:
#                 print y
#                 p = True
#         if p == False:
#             print i

In [101]:
# # Dipendenze esclusive di scanr: TANTE!!
# con = []
# for i in final_dep_results_copy["scanr"]["fds"]:
#     if i not in inter_fds:
#         p = False
#         for y in inter_fds:
#             if i <= y:
#                 p = True
#         if p == False:
#             print i
#             con.append(i)

In [102]:
# # Provo le FD esclusive di scanr su openaire, ma scremo togliendo quelle in cui:
# # Il RHS su openaire consiste in un attributo nullo
# # Il LHS in cui tra i suoio elementi ci sono attributi per openaire nulli 
# ####### ATTENZIONE in verità potrei togliere solo
#       # quel particolare attributo e guardare quella dipendenza
    
#       # Fatto! Esclude gli RHS null e toglie le parti nunll dai lhs. Dovrebbe andare
# con_screm = []
# for i in con:
#     if stats["openaire"]["Percentage of Nulls"][attributes[i.rhs[0]]] != 100:
#         good = True
#         new_i = deepcopy(i)
#         for x in i.lhs:
#             print "esamino {}".format(x)
#             print stats["openaire"]["Percentage of Nulls"][attributes[x]]
#             print "-----"
#             if stats["openaire"]["Percentage of Nulls"][attributes[x]] == 100:
#                 new_i.lhs.remove(x)
        
#         print new_i
#         if new_i not in con_screm:
#             con_screm.append(new_i)
    

In [29]:
a = FD(['1'], ['2'] )
b = deepcopy(a)
b.lhs = ['1', '2']
print a

['1'] -> ['2']


In [33]:
for i in con_screm:
    print i

['7', '4'] -> ['8']
['7', '4'] -> ['2']
['4', '26'] -> ['2']
['2', '4'] -> ['26']
['4'] -> ['2']
['4'] -> ['12']
['4'] -> ['7']
['8', '4'] -> ['2']
['8', '4'] -> ['12']
['8', '4'] -> ['7']
['4', '12'] -> ['2']
['4', '12'] -> ['7']
['4'] -> ['8']
['4'] -> ['26']
['2', '4'] -> ['8']
['2', '4'] -> ['12']
['4', '12'] -> ['8']
['7', '26'] -> ['12']
['7', '8', '26'] -> ['12']
['2', '7', '26'] -> ['12']
['2', '7', '8', '26'] -> ['12']
['7', '26'] -> ['8']
['7', '26', '12'] -> ['8']
['7', '23', '26', '12'] -> ['8']
['2', '7', '12'] -> ['8']
['2', '7', '23', '12'] -> ['8']
['7'] -> ['8']
['7'] -> ['12']
['7', '8'] -> ['12']
['7', '12'] -> ['8']
['7', '23', '12'] -> ['8']
['2', '7'] -> ['8']
['2', '7'] -> ['12']
['2', '7', '8'] -> ['12']
['26', '12'] -> ['8']
['26'] -> ['8']
['2', '26'] -> ['8']
['2', '12'] -> ['8']
['12'] -> ['8']
[] -> ['8']


In [181]:
# A questo punto devo aprire i csv e trovare le tuple che invalidano le dipendenze.
# es se ho i csv A e B dove A ha una dipendenza x che B non ha, vado ad analizzare le sue tuple e trovare le responsabili
prova = pd.read_csv('/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_OpenAire.csv', sep=',')

In [ ]:
def bing_bing_bong(a_list):    
    eccez = []
    for _, g in prova.groupby([attributes[i] for i in a_list[:-1]]):
        if len(g) > 1:
            a = g[attributes[a_list[-1]]]
            #print len(a.unique()) 
            if len(a.unique()) != 1:
                eccez.append(a)
    return eccez
    #pd.concat(g for _, g in df.groupby("ID") if len(g) > 1)

In [182]:
a_list = ['2', '7', '8', '26', '12']
a = bing_bing_bong(a_list)
for i in a:
    print i

11910    25124
16839    25100
Name: postcode, dtype: object


In [87]:
len(a)

1

In [85]:
print attributes['2']
print attributes['12']
print attributes['8']

acronyms
postcode
city


In [43]:
pd.options.display.max_colwidth = 200

In [103]:
stats["openaire"]["Percentage of Nulls"][attributes['3']]

100

In [154]:
# Esclusive (senza nulle e ucc)
print "Len di con: {} \nLen di con_screm: {}".format(len(con), len(con_screm))

Len di con: 2002 
Len di con_screm: 326


In [71]:
# Tutte
len(final_dep_results["scanr"]["fds"])

2921

In [75]:
# Togliendo nulle e ucc
len(final_dep_results_copy["scanr"]["fds"])

2259

In [91]:
# Non corretto

# for i in final_dep_results_copy["scanr"]["fds"]:
#     if i not in inter_fds:
#         print i


In [92]:
# for i in final_dep_results["scanr"]["uccs"]:
#     #if set(['2', '29', '7', '9', '19', '26']) == set(i.comb):
#     if set(['4', '7', '5']) == set(i.comb):
#         print i
# #     if len(i.comb) == 3:
# #         print i

In [93]:
# for i in final_dep_results["openaire"]["fds"]:
#     if set(['7', '4']) <= set(i.lhs):
#         print i

In [94]:
# aaa = ['1', '7', '26']
# set(['2', '26']) <= set(aaa)

In [89]:
pd.set_option('display.max_columns', 500)

In [90]:
#a_list = ['7', '4', '8']
#prova[[attributes[i] for i in a_list]]
#for index, row in prova.iterrows():
prova.iloc[[11910, 16839]]


id acronyms  alias                    label  creationYear  \
11910  404096      A2A    NaN                  A2A SPA           NaN   
16839  412259      A2A    NaN  A2A RETI ELETTRICHE SPA           NaN   

       commercialLabel            address     city  citycode country  \
11910              NaN  VIA LAMARMORA 230  BRESCIA       NaN   Italy   
16839              NaN  VIA LAMARMORA 230  BRESCIA       NaN   Italy   

      countryCode postcode  urbanUnit  urbanUnitCode  lat  lon  revenueRange  \
11910          IT    25124        NaN            NaN  0.0  0.0           NaN   
16839          IT    25100        NaN            NaN  0.0  0.0           NaN   

       privateFinanceDate  employees  typeCategoryCode  typeLabel  typeKind  \
11910                 NaN        NaN               NaN        NaN       NaN   
16839                 NaN        NaN               NaN        NaN       NaN   

        isPublic  leaders  staff                links  privateOrgTypeId  \
11910  undefined      NaN    NaN  https://www.a2a.eu/               NaN   
16839  undefined      NaN    NaN  https://www.a2a.eu/               NaN   

       privateOrgTypeLabel  activities  relations  badges  children  \
11910                  NaN         NaN        NaN     NaN       NaN   
16839                  NaN         NaN        NaN     NaN       NaN   

                                                                                                                                                                   identifiers  
11910  lid_openaire_id_oai:dnet:corda__h2020::4e7b326609d91372847a0b1da410cc30,PID_986400858;PID_986400858;openaire_id_oai:dnet:corda__h2020::4e7b326609d91372847a0b1da410cc30  
16839  openaire_id_oai:dnet:corda_______::2d2bc99798c30ba83e75e31606575a00;lid_openaire_id_oai:dnet:corda_______::2d2bc99798c30ba83e75e31606575a00,PID_992788017;PID_992788017

In [95]:
# prova[[attributes[i] for i in a_list]]

In [96]:
# prova[[attributes[i] for i in a_list]].iloc[33940][2]

In [97]:
# prova[[attributes[i] for i in a_list]].iloc[33941][2]

In [35]:
def bing_bing_bong(a_list):    
    eccez = []
    for _, g in prova.groupby([attributes[i] for i in a_list[:-1]]):
        if len(g) > 1:
            a = g[attributes[a_list[-1]]]
            #print len(a.unique()) 
            if len(a.unique()) != 1:
                eccez.append(a)
    return eccez
    #pd.concat(g for _, g in df.groupby("ID") if len(g) > 1)

In [144]:
for i in eccez:
    print i

1833     PLANEGG MARTINSRIED
11595            MARTINSRIED
Name: city, dtype: object
3240              PARIS
12124    PARIS CEDEX 08
Name: city, dtype: object
939     BERN
2747    BERN
6166    Bern
Name: city, dtype: object
977     Osnabrueck
4272     Osnabrück
5089     Osnabrück
Name: city, dtype: object
2112    HANNOVER
9878    Hannover
Name: city, dtype: object
11122    BERN
13062    Bern
16808    BERN
Name: city, dtype: object
7586           Seitenstetten
15740    SEITENSTETTEN MARKT
Name: city, dtype: object
4458    PARIS
7542    BALMA
Name: city, dtype: object
525      TORTONA ALESSANDRIA
12152                TORTONA
Name: city, dtype: object
4951        ROMA
12437    ROMA RM
Name: city, dtype: object
14076      MILANO
14431    CORBETTA
Name: city, dtype: object


In [113]:
pd.concat(g for _, g in prova[[attributes[j] for j in a_list]].groupby([attributes[i] for i in a_list[:-1]]) if len(g) > 1)

ValueError: No objects to concatenate

In [192]:
a_list = ['4', '26', '5']


In [193]:
x = prova[["id", "label", "links", "creationYear"]].groupby([attributes[i] for i in a_list[:-1]], as_index = False).count()

In [189]:
x

label  \
0                                                                                                   ''PROESYS S.R.L.''   
1                                                                                                       -SKOPIA S.R.L.   
2             00124 S.R.L. START-UP COSTITUITA A NORMA DELL'ART. 4 COMMA 10 BIS DEL DECRETO LEGGE 24 GENNAIO 2015 N. 3   
3                                                                                                    01 INDUSTRIES SRL   
4                                                                  01 SOCIETA' A RESPONSABILITA' LIMITATA SEMPLIFICATA   
5                                                                                          012 FACTORY CALABRIA S.R.L.   
6                                                                                                    012FACTORY S.R.L.   
7                                                                                                        081LAB S.R.L.   
8                                                                0ICS SOCIETA' A RESPONSABILITA' LIMITATA SEMPLIFICATA   
9                                                                                                  1 2 3 PRONTO S.R.L.   
10                                                                      1 HEARTNET SOCIETA' A RESPONSABILITA' LIMITATA   
11                                                                                                         1177 S.R.L.   
12                                                                                                          142 S.R.L.   
13                                                                                                           14SPM SRL   
14           16BIT S.R.L. start-up costituita a norma dell'art. 4 comma 10 bis del decreto legge 24 gennaio 2015, n. 3   
15                                                                                              1813 INTRAPRESA S.R.L.   
16           1849 C S.R.L. START-UP COSTITUITA A NORMA DELL'ART.4 COMMA 10 BIS DEL DECRETO LEGGE 24 GENNAIO 2015, N. 3   
17                                                                                                     18MONTHS S.R.L.   
18                                                                                                              1B SRL   
19                                                                                                     1STICKET S.R.L.   
20                                                                                                         1SUN S.R.L.   
21                                                                                                      1TRUEID S.R.L.   
22                                                                                                        2 PAY S.P.A.   
23                                                                                                     2-TORRI.COM SRL   
24                                                                                      2038 INNOVATION COMPANY S.R.L.   
25                                                                                                    2045 TECH S.R.L.   
26                                                                         21 WARE SOCIETA' A RESPONSABILITA' LIMITATA   
27                                                                                                            221E SRL   
28                                                                                                         24-7 S.R.L.   
29                                                                                                        247TD S.R.L.   
...                                                                                                                ...   
8019                                                         ZEBULONI SOCIETA' A RESPONSABILITA' LIMITATA SEMPLIFICATA   
8020                                                           ZEESTY SOCIETA' A RESPON

In [194]:
for i in x["id"]:
    if i != 1:
        print "aaa"

In [2]:
#from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual


In [159]:
a_list

['4', '26', '5']

In [161]:
print attributes["4"]
print attributes["26"]
print attributes["5"]

label
links
creationYear


In [78]:
def f(x):
    return x

In [107]:
interact(f, x=10);

aW50ZXJhY3RpdmUoY2hpbGRyZW49KEludFNsaWRlcih2YWx1ZT0xMCwgZGVzY3JpcHRpb249dSd4JywgbWF4PTMwLCBtaW49LTEwKSwgT3V0cHV0KCkpLCBfZG9tX2NsYXNzZXM9KHUnd2lkZ2XigKY=


# Parte sui grafici

In [ ]:

from ipywidgets import Layout

import scipy as sp
import plotly
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.io as pio
#from scipy import stats
import os


import plotly.io as pio
init_notebook_mode(connected=True)

urls_dict = {}

In [ ]:
out = []
for i in xrange(len(attributes.keys())):
    out.append(widgets.Output())
#out1 = widgets.Output()
#out2 = widgets.Output()


tab = widgets.Tab(children = out)
for name, i in zip(attributes.keys(), xrange(len(attributes.keys()))):
        tab.set_title(i, name)

display(tab)
traces = []
plots_urls = {}
#low_games = games_with_description[games_with_description['Global_Sales'] < np.percentile(games_with_description['Global_Sales'], 10)]
for outi, attr in zip(out, attributes.keys()):
    with outi:
        trace = go.Bar(
            x=ds_names,
            y= [100 - stats[name]["Percentage of Nulls"][attr] for name in ds_names],  #Top 10 frequent items
            name='bars'
    #             boxmean=True,
    #             marker={'color': c[i]}
            )

            #traces.append(trace)

        layout = go.Layout(
        title = 'Percentage of non-Nulls for attribute: ' + attr,
        yaxis = dict(title='Percentage'),
        xaxis = dict(title='', tickangle=90), 
        height = 600,
        width = 700
    )
        fig = go.Figure(data=[trace], layout=layout)
        iplot(fig, show_link=True)
        #plot(fig, filename="/home/marco/Img_Ris/No_null_perc_attr/" + attr, image='png', auto_open=False)
        #plot(fig, output_type='div', image_filename='ciao', image='png', auto_open=False)
        directory = "Img_Ris/No_null_perc_attr/"
        if not os.path.exists(directory):
            os.makedirs(directory)
        directory = "Html_files/No_null_perc_attr/"
        if not os.path.exists(directory):
            os.makedirs(directory)
        pio.write_image(fig, 'Img_Ris/No_null_perc_attr/' + attr + '.png')
        plots_urls[attr] = re.sub(r".*marco/", "", plot(fig, auto_open=False, filename="Html_files/No_null_perc_attr/" + attr + ".html"))
urls_dict["Data_grouped_by_attribute"] = plots_urls


In [ ]:
# Percentuale di non nulli per ogni dataset
# X -> attributi
# Y -> percentuale
out = []
for i in xrange(len(ds_names)):
    out.append(widgets.Output())
#out1 = widgets.Output()
#out2 = widgets.Output()


tab = widgets.Tab(children = out)
for name, i in zip(ds_names, xrange(len(ds_names))):
        tab.set_title(i, name)

display(tab)
traces = []
plots_urls = {}
#low_games = games_with_description[games_with_description['Global_Sales'] < np.percentile(games_with_description['Global_Sales'], 10)]
for outi, name in zip(out, ds_names):
    with outi:
        trace = go.Bar(
            x=list(stats[name].index),
            y=[100 - stats[name]["Percentage of Nulls"][attr] for attr in stats[name].index],  #Top 10 frequent items
            name='bars'
    #             boxmean=True,
    #             marker={'color': c[i]}
            )

            #traces.append(trace)

        layout = go.Layout(
        title = 'Percentage of non-Nulls for dataset: ' + name,
        yaxis = dict(title='Count'),
        xaxis = dict(title='Items', tickangle=90),
        height = 600,
        width = 700
    )
        fig = go.Figure(data=[trace], layout=layout)
        iplot(fig)
        directory = "Img_Ris/No_null_perc_ds/"
        if not os.path.exists(directory):
            os.makedirs(directory)
        pio.write_image(fig, 'Img_Ris/No_null_perc_ds/' + name + '.png')
        directory = "Html_files/No_null_perc_ds/"
        if not os.path.exists(directory):
            os.makedirs(directory)
        plots_urls[name] = re.sub(r".*marco/", "", plot(fig, auto_open=False, filename="Html_files/No_null_perc_ds/" + name + ".html"))
urls_dict["Data_grouped_by_country"] = plots_urls


In [ ]:
# Salvo i nomi dei grafici singoli senza tab, in modo da averli comodi per il Report
single_charts = []

In [ ]:
base_name = ds_names[0]
base_name

In [ ]:
# Media delle medie
media = defaultdict(float)
#for attr in stats["orcid"].index: # TODO: devo mettere qualcosa di più generico
for attr in stats[base_name].index: # Penso possa bastare
    for name in ds_names:
        media[attr] += (100 - stats[name]["Percentage of Nulls"][attr])
        
    media[attr] = media[attr] / len(ds_names)
    

In [ ]:
trace = go.Bar(
            x=list(stats[base_name].index),
            y=[media[attr] for attr in stats[name].index],  #Top 10 frequent items
            name='bars'
    #             boxmean=True,
    #             marker={'color': c[i]}
            )

            #traces.append(trace)

layout = go.Layout(
title = 'Non-Nulls mean for every attribute',
yaxis = dict(title='Count'),
xaxis = dict(title='Items', tickangle=90),
height = 800,
width = 800
)
fig = go.Figure(data=[trace], layout=layout)
#iplot(fig, filename='prova.html')
iplot(fig)
directory = "Img_Ris/"
if not os.path.exists(directory):
    os.makedirs(directory)
pio.write_image(fig, 'Img_Ris/No_null_mean.png')
urls_dict["Mean_for_country"] = re.sub(r".*marco/", "", plot(fig, auto_open=False, filename="Html_files/No_null_mean.html"))
single_charts.append("Mean_for_country")    


In [ ]:
aiuto = {}

In [ ]:
traces= []
for attr in stats[base_name].index:
    misure = []
    for name in ds_names:
        misure.append(stats[name]["Percentage of Nulls"][attr])
    
    aiuto[attr] = misure    
    trace = go.Box(
        #x = list(stats["orcid"].index),
        y=np.array(misure),
        name=attr,
        boxmean=True,
        #marker={'color': c[i]}
    )
    traces.append(trace)

layout = go.Layout(
    title='Boxplot of means',
    showlegend=False,
    yaxis=dict(
        title='Percentage of Nulls'
    ),
    height=800, width=800
#     margin=go.Margin(
#         l=100,
#         r=50,
#         b=100,
#         t=100,
#         pad=4
#     )
)
fig = go.Figure(data=traces, layout=layout)
iplot(fig)
directory = "Img_Ris/"
if not os.path.exists(directory):
    os.makedirs(directory)
pio.write_image(fig, 'Img_Ris/Boxplot_mean.png')
urls_dict["Mean_distribution"] = re.sub(r".*marco/", "", plot(fig, auto_open=False, filename="Html_files/Boxplot_mean.html"))
single_charts.append("Mean_distribution")    


In [ ]:
# % righe non nulle considerando tutte le righe di tutti i ds
perc_r = defaultdict(float)
for attr in stats[base_name].index:
    somma = 0
    for name in ds_names:
        perc_r[attr] += stats[name]["Number of Tuples"][attr] - stats[name]["Nulls"][attr]
        somma += stats[name]["Number of Tuples"][attr]
    perc_r[attr] = 100 * perc_r[attr] / somma

In [ ]:
trace = go.Bar(
            x=list(stats[base_name].index),
            y=[perc_r[attr] for attr in stats[name].index],  #Top 10 frequent items
            name='bars'
    #             boxmean=True,
    #             marker={'color': c[i]}
            )

            #traces.append(trace)

layout = go.Layout(
title = 'Percentage of Non-Null rows for every attribute',
yaxis = dict(title='Count'),
xaxis = dict(title='Items', tickangle=90),
height = 800,
width = 800
)
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)
directory = "Img_Ris"
if not os.path.exists(directory):
    os.makedirs(directory)
pio.write_image(fig, 'Img_Ris/Perc_no_null_rows.png')
urls_dict["Overall_coverage_percentage"] = re.sub(r".*marco/", "", plot(fig, auto_open=False, filename="Html_files/Perc_no_null_rows.html"))
single_charts.append("Overall_coverage_percentage")    


In [ ]:
# Media righe non nulle considerando tutte le righe di tutti i ds
media_r = defaultdict(float)
for attr in stats[base_name].index:
    #somma = 0
    for name in ds_names:
        media_r[attr] += stats[name]["Number of Tuples"][attr] - stats[name]["Nulls"][attr]
        #somma += stats[name]["Number of Tuples"][attr]
    media_r[attr] = media_r[attr] / len(ds_names)

In [ ]:
trace = go.Bar(
            x=list(stats[base_name].index),
            y=[media_r[attr] for attr in stats[name].index],  
            name='bars'
    #             boxmean=True,
    #             marker={'color': c[i]}
            )

            #traces.append(trace)

layout = go.Layout(
title = 'Non-Null mean (rows) for every attribute',
yaxis = dict(title='Count'),
xaxis = dict(title='Items', tickangle=90),
height = 800,
width = 800
)
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)
directory = "Img_Ris"
if not os.path.exists(directory):
    os.makedirs(directory)
pio.write_image(fig, 'Img_Ris/No_null_mean_rows.png')
urls_dict["Overall_coverage"] = re.sub(r".*marco/", "", plot(fig, auto_open=False, filename="Html_files/No_null_mean_rows.html"))
single_charts.append("Overall_coverage") 

In [ ]:
single_charts

In [ ]:
urls_dict

In [ ]:
def tabs(name):
    html_string = '''<h3><a href="#''' + name + '''" data-toggle="collapse">''' + name + '''</a></h3>
    <div class="well">
    <div id="''' + name + '''" class="collapse in">
    <ul class="nav nav-pills">'''
    #tabs(html_string, "No_null_perc_attr")
    #tabs(html_string, "No_null_perc_ds")
    first = True
#     if name.split('_')[-1] == "ds":
#         substitute = ds_names
#     elif name.split('_')[-1] == "attr":
#         substitute = stats[base_name].index
#     else:
#         print "dati non supportati, deve terminare con attr o ds"
    if name.split('_')[-1] == "country":
        substitute = ds_names
    elif name.split('_')[-1] == "attribute":
        substitute = stats[base_name].index
    else:
        print "dati non supportati, deve terminare con attr o ds"

        raise error
    for el in substitute:
    # for attr in ["id"]:
        if first:
            first= False
            html_string += '''
            <li class="active"> <a data-toggle="tab" href="#''' + el.replace(" ", "") + '''">''' + el + '''</a> </li>'''
        else:
            html_string += '''
            <li> <a data-toggle="tab" href="#''' + el.replace(" ", "") + '''">''' + el + '''</a> </li>'''
    html_string += '''
        </ul>
        <div class="tab-content">
    '''

    first = True
#     if name.split('_')[-1] == "ds":
#         substitute = ds_names
#     elif name.split('_')[-1] == "attr":
#         substitute = stats[base_name].index
#     else:
#         print "dati non supportati, deve terminare con attr o ds"
#         raise error
    if name.split('_')[-1] == "country":
        substitute = ds_names
    elif name.split('_')[-1] == "attribute":
        substitute = stats[base_name].index
    else:
        print "dati non supportati, deve terminare con attr o ds"

        raise error
    for el in substitute:
    # for url, attr in zip(plots_urls[0], ["id"]):
        print "urls_dict[{}][{}] = {} \n".format(name, el, urls_dict[name][el])
        if first:
            html_string += '''    
            <div id="''' + el.replace(" ", "") + '''" class="tab-pane fade in active" align="center">
              <p><iframe width="700" height="600" frameborder="0" seamless="seamless" scrolling="no" src="''' + urls_dict[name][el].replace(" ", "%20") + '''"></iframe></p>
            </div>
            '''
            first = False
        else:
            html_string += '''    
            <div id="''' + el.replace(" ", "") + '''" class="tab-pane fade" align="center">
              <p><iframe width="700" height="600" frameborder="0" seamless="seamless" scrolling="no" src="''' + urls_dict[name][el].replace(" ", "%20") + '''"></iframe></p>
            </div>
            '''


    html_string += '''
        </div>
        </div>
        </div>
    '''
    return html_string

In [ ]:
def one_chart(name):
    html_string = '''
    <h3><a href="#''' + name + '''" data-toggle="collapse">''' + name + '''</a></h3>
    <div class="well">
        <div id="''' + name + '''" class="collapse in"align="center">
            <p><iframe width="800" height="800" frameborder="0" seamless="seamless" scrolling="no" src="''' + urls_dict[name] + '''"></iframe></p>
        </div>
    </div>
    '''
    return html_string
    

In [ ]:
html_string = '''
<!DOCTYPE html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width = device-width, initial-scale = 1">
  <title>Report</title>
  <link rel="stylesheet" type="text/css" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.3.5/css/bootstrap.min.css">
  <style>
 .jumbotron{
     background-color:#2E2D88;
     color:white;
 }
 /* Adds borders for tabs */
 .tab-content {
     border-top: 1px solid #ddd;
     border-left: 1px solid #ddd;
     border-right: 1px solid #ddd;
     border-bottom: 1px solid #ddd;
     background: #29bdc1;
     padding: 10px;

 }
 .container {
     background: whitesmoke;
 }
 .nav-tabs {
     margin-bottom: 0;
 }
 </style>
</head>
<body>
  <div class="container">
    <div class="page-header">
        <h1>Report</h1>
    </div>'''

# html_string += tabs("No_null_perc_attr")
# html_string += tabs("No_null_perc_ds")
html_string += tabs("Data_grouped_by_attribute")
html_string += tabs("Data_grouped_by_country")
for name in single_charts:
    html_string += one_chart(name)
html_string += '''  </div> 
<script src="https://ajax.googleapis.com/ajax/libs/jquery/2.1.3/jquery.min.js"></script>
<script src="https://maxcdn.bootstrapcdn.com/bootstrap/3.3.5/js/bootstrap.min.js"></script>
</body>
</html>
'''


In [ ]:
f = open('/home/marco/report.html','w')
f.write(html_string.encode("utf-8"))  # Serve l'utf per stmpare stringhe strane!!!!!
f.close()

# Parte sulle dipendenze risultanti

### INDs minime comuni

In [ ]:
for i in inter_inds_min:
    print i

### FDs minime comuni

In [29]:
for i in inter_fds_min:
    print i

[] -> ['6']
['33'] -> ['4']
['33'] -> ['1']
[] -> ['16']
[] -> ['15']
['1'] -> ['4']
['1'] -> ['33']


### UCCs minime comuni

In [ ]:
for i in inter_uccs_min:
    print i

### INDs comuni

In [117]:
for i in inter_inds:
    print i

### FDs comuni
# ATTENZIONE: perché tra i comuni c'è []->[6, 15, 16] e non con [1]????
# L'algoritmmo dovrebbe prendere gli insiemi comuni, quindi 1 e non []

In [37]:
attributes

{'1': 'id',
 '10': 'country',
 '11': 'countryCode',
 '12': 'postcode',
 '13': 'urbanUnit',
 '14': 'urbanUnitCode',
 '15': 'lat',
 '16': 'lon',
 '17': 'revenueRange',
 '18': 'privateFinanceDate',
 '19': 'employees',
 '2': 'acronyms',
 '20': 'typeCategoryCode',
 '21': 'typeLabel',
 '22': 'typeKind',
 '23': 'isPublic',
 '24': 'leaders',
 '25': 'staff',
 '26': 'links',
 '27': 'privateOrgTypeId',
 '28': 'privateOrgTypeLabel',
 '29': 'activities',
 '3': 'alias',
 '30': 'relations',
 '31': 'badges',
 '32': 'children',
 '33': 'identifiers',
 '4': 'label',
 '5': 'creationYear',
 '6': 'commercialLabel',
 '7': 'address',
 '8': 'city',
 '9': 'citycode'}

In [44]:
for i in inter_fds:
    #if i.lhs == ['1'] or i.lhs == []:
    #if len(i.lhs) == 1:
    s = ""
    for el in i.lhs:
        s += attributes[str(el)] + " "
    s += "-> "
    for el in i.rhs:
        s += attributes[str(el)] + " "
    print s

id -> acronyms 
identifiers -> acronyms 
id -> alias 
identifiers -> alias 
citycode label -> alias 
city label -> alias 
label urbanUnit -> alias 
creationYear label -> alias 
-> commercialLabel 
id -> address 
identifiers -> address 
id -> citycode 
identifiers -> citycode 
badges label links urbanUnit -> citycode 
employees label links urbanUnit -> citycode 
city label -> citycode 
id -> country 
identifiers -> country 
city label staff -> country 
city label urbanUnit -> country 
countryCode -> country 
id -> countryCode 
identifiers -> countryCode 
city label staff -> countryCode 
city label urbanUnit -> countryCode 
country -> countryCode 
id -> postcode 
identifiers -> postcode 
id -> urbanUnitCode 
identifiers -> urbanUnitCode 
address label -> urbanUnitCode 
city label -> urbanUnitCode 
label postcode -> urbanUnitCode 
activities creationYear label -> urbanUnitCode 
label urbanUnit -> urbanUnitCode 
address city postcode privateOrgTypeId -> urbanUnitCode 
address city postcode

In [60]:
for x in xrange(1, 34):
    print x
    for i in inter_fds:
        if i.lhs == [str(x)]:
            print  i

1
['1'] -> ['2']
['1'] -> ['3']
['1'] -> ['7']
['1'] -> ['9']
['1'] -> ['10']
['1'] -> ['11']
['1'] -> ['12']
['1'] -> ['14']
['1'] -> ['17']
['1'] -> ['18']
['1'] -> ['19']
['1'] -> ['20']
['1'] -> ['22']
['1'] -> ['23']
['1'] -> ['24']
['1'] -> ['25']
['1'] -> ['30']
['1'] -> ['31']
['1'] -> ['32']
['1'] -> ['33']
['1'] -> ['4']
['1'] -> ['26']
['1'] -> ['5']
['1'] -> ['8']
['1'] -> ['29']
['1'] -> ['13']
['1'] -> ['27']
['1'] -> ['28']
['1'] -> ['21']
2
3
4
['4'] -> ['30']
5
6
7
8
9
['9'] -> ['14']
10
['10'] -> ['11']
11
['11'] -> ['10']
12
13
14
15
16
17
18
19
20
['20'] -> ['22']
21
['21'] -> ['20']
['21'] -> ['22']
22
23
24
25
26
27
['27'] -> ['28']
28
['28'] -> ['27']
29
30
31
32
33
['33'] -> ['2']
['33'] -> ['3']
['33'] -> ['7']
['33'] -> ['9']
['33'] -> ['10']
['33'] -> ['11']
['33'] -> ['12']
['33'] -> ['14']
['33'] -> ['17']
['33'] -> ['18']
['33'] -> ['19']
['33'] -> ['20']
['33'] -> ['22']
['33'] -> ['23']
['33'] -> ['24']
['33'] -> ['25']
['33'] -> ['30']
['33'] -> ['31']


In [64]:
for i in inter_fds:
    if len(i.lhs) == 2:
        print  i

['9', '4'] -> ['3']
['8', '4'] -> ['3']
['4', '13'] -> ['3']
['5', '4'] -> ['3']
['8', '4'] -> ['9']
['7', '4'] -> ['14']
['8', '4'] -> ['14']
['4', '12'] -> ['14']
['4', '13'] -> ['14']
['7', '13'] -> ['14']
['12', '13'] -> ['14']
['7', '4'] -> ['18']
['4', '17'] -> ['18']
['4', '26'] -> ['18']
['4', '12'] -> ['18']
['8', '4'] -> ['18']
['5', '4'] -> ['20']
['7', '4'] -> ['22']
['4', '26'] -> ['22']
['9', '4'] -> ['22']
['8', '4'] -> ['22']
['4', '12'] -> ['22']
['31', '4'] -> ['22']
['4', '13'] -> ['22']
['4', '14'] -> ['22']
['4', '27'] -> ['22']
['4', '28'] -> ['22']
['5', '4'] -> ['22']
['19', '4'] -> ['22']
['23', '4'] -> ['22']
['23', '26'] -> ['22']
['23', '18'] -> ['22']
['7', '26'] -> ['30']
['7', '17'] -> ['30']
['7', '19'] -> ['30']


In [65]:
for i in inter_fds:
    if len(i.lhs) == 3:
        print  i

['8', '4', '25'] -> ['10']
['8', '4', '13'] -> ['10']
['8', '4', '25'] -> ['11']
['8', '4', '13'] -> ['11']
['29', '5', '4'] -> ['14']
['7', '4', '26'] -> ['17']
['7', '4', '24'] -> ['17']
['7', '31', '4'] -> ['17']
['7', '4', '27'] -> ['17']
['7', '4', '28'] -> ['17']
['7', '5', '4'] -> ['17']
['7', '19', '4'] -> ['17']
['7', '4', '20'] -> ['17']
['7', '4', '21'] -> ['17']
['9', '4', '26'] -> ['17']
['8', '4', '26'] -> ['17']
['4', '26', '12'] -> ['17']
['4', '26', '13'] -> ['17']
['8', '4', '24'] -> ['17']
['4', '24', '12'] -> ['17']
['31', '8', '4'] -> ['17']
['8', '4', '27'] -> ['17']
['8', '4', '28'] -> ['17']
['8', '5', '4'] -> ['17']
['8', '19', '4'] -> ['17']
['31', '4', '12'] -> ['17']
['4', '12', '27'] -> ['17']
['4', '12', '28'] -> ['17']
['5', '4', '12'] -> ['17']
['19', '4', '12'] -> ['17']
['5', '4', '13'] -> ['17']
['19', '4', '24'] -> ['18']
['8', '4', '26'] -> ['19']
['7', '4', '26'] -> ['20']
['7', '4', '24'] -> ['20']
['7', '31', '4'] -> ['20']
['29', '7', '4'] -> ['

In [66]:
for i in inter_fds:
    if '9' in i.lhs:
        print  i

['9', '4'] -> ['3']
['9'] -> ['14']
['9', '4', '26'] -> ['17']
['9', '4', '26'] -> ['20']
['9', '4', '24'] -> ['20']
['31', '9', '4'] -> ['20']
['29', '9', '4'] -> ['20']
['9', '4', '27'] -> ['20']
['9', '4', '28'] -> ['20']
['9', '19', '4'] -> ['20']
['9', '4', '17'] -> ['20']
['9', '4'] -> ['22']
['7', '9', '19', '26', '27'] -> ['22']
['7', '9', '19', '26', '28'] -> ['22']
['7', '9', '19', '24', '27'] -> ['22']
['7', '9', '19', '24', '28'] -> ['22']
['7', '9', '23', '24'] -> ['22']
['2', '7', '9', '23'] -> ['22']
['7', '31', '9', '19', '27'] -> ['22']
['7', '31', '9', '19', '28'] -> ['22']
['7', '31', '9', '23'] -> ['22']
['7', '9', '5', '27'] -> ['22']
['7', '9', '27', '17'] -> ['22']
['7', '9', '5', '28'] -> ['22']
['7', '9', '28', '17'] -> ['22']
['2', '29', '9', '26', '27', '17'] -> ['22']
['2', '29', '9', '26', '28', '17'] -> ['22']
['2', '9', '5', '26', '27', '17'] -> ['22']
['2', '9', '5', '26', '28', '17'] -> ['22']
['29', '9', '5', '26', '27'] -> ['22']
['29', '9', '19', '26

### UCCs comuni

In [ ]:
for i in inter_uccs:
    print i

In [ ]:
# Intersezioni MINIME COMUNI (NO NULL)
inter_inds_min_no_null = intersection_all("inds", final_dep_results_no_null)
inter_fds_min_no_null = intersection_all("fds",final_dep_results_no_null)
#inter_uccs_min_no_null = intersection_all("uccs", final_dep_results_no_null)

#Le UCC non ha senso ricalcorarle

In [ ]:
# Intersezioni COMUNI
inter_inds_no_null = intersection_all_ign("inds", final_dep_results_no_null)
inter_fds_no_null = intersection_all_ign("fds", final_dep_results_no_null)
#inter_uccs_no_null = intersection_all_ign("uccs", final_dep_results_no_null)

### INDS minime comuni (no_null)

In [ ]:
for i in inter_inds_min_no_null:
    print i

### FDs minime comuni (no_null)

In [ ]:
for i in inter_fds_min_no_null:
    print i

### INDs comuni (no_null)

In [ ]:
for i in inter_inds_no_null:
    print i

### FDs comuni (no_null)

In [ ]:
for i in inter_fds_no_null:
    print i

## Comandi di utility. Ci sono ancora da inserire da qualche parte.

In [2]:
mypath = "/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData"

In [21]:
# Per modificare i nomi di tutti i file in una cartella
for f in listdir(mypath):
    if isfile(join(mypath, f)) and len(f)>64:
#         i = f.index(".")
#         new_f = f[:i] + "After" + f[i:]
#         print new_f
#         rename(mypath + "/" + f, mypath + "/" + new_f)
        new_f = f[0:60]  + ".csv"
        print new_f
        rename(mypath + "/" + f, mypath + "/" + new_f)
    
#onlyfiles_in

#Se ho dei nomi di file tropop lunghi

In [11]:
# Lista di tutti i File Input
def all_ds_info():
    url = 'http://127.0.0.1:8081/api/file-inputs'
    #print url
    r = requests.get(url)
    resp_jsosn = json.loads(r.content)
    return resp_jsosn

In [12]:
all_ds_info()

[{u'comment': None,
  u'escapeChar': u'',
  u'fileName': u'/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_Crawled.csv',
  u'hasHeader': True,
  u'id': 715,
  u'ignoreLeadingWhiteSpace': True,
  u'name': u'/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_Crawled.csv',
  u'nullValue': u'',
  u'quoteChar': u'"',
  u'separator': u',',
  u'skipDifferingLines': False,
  u'skipLines': 0,
  u'strictQuotes': False,
  u'type': u'fileInput'},
 {u'comment': None,
  u'escapeChar': u'',
  u'fileName': u'/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_Crawled.csv',
  u'hasHeader': True,
  u'id': 715,
  u'ignoreLeadingWhiteSpace': True,
  u'name': u'/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/organizations_Crawled.csv',
  u'nullValue': u'',
  u'quoteChar': u'"',
  u'separator': u',',
  u'skipDifferingLines': False,
  u'skipLines': 0,
  u'strictQuotes': False,
  u'type': u'fileInput'},
 {u'comment': None,
  u'

In [5]:
# Passando l'id di un ds, lo elimino
def del_ds(ds_id):
    url = 'http://127.0.0.1:8081/api/file-inputs/delete/' + str(ds_id)
    #print url
    r = requests.delete(url)
    return r.content
#     resp_json = json.loads(r.content)
#     for alg in resp_json:
#         if alg_name in alg["fileName"]:
# 

In [6]:
# Cancello tutti i ds, faccio un reset

def del_all_ds():
    info = all_ds_info()
    for i in info:
        del_ds(i["id"])

In [7]:
del_all_ds()

In [11]:
def del_all_ex():
    for i in xrange(10000):
        url = 'http://127.0.0.1:8081/api/executions/delete/' + str(i)
        r = requests.delete(url)
        

In [8]:
url = 'http://127.0.0.1:8081/api/executions/delete/1992'
r = requests.delete(url)
        

In [12]:
del_all_ex()

In [8]:
# Mi permette di inserire in metanome un ds
def post_ds(ds_path):
        headers = {
        #"Host": "localhost:8081",
        "User-Agent": "Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:65.0) Gecko/20100101 Firefox/65.0",
        "Accept": "application/json, text/plain, */*",
        "Accept-Language": "it-IT,it;q=0.8,en-US;q=0.5,en;q=0.3",
        #"Accept-Encoding": "gzip, deflate",
        "Referer": "http://localhost:8080/",
        "Content-Type":"application/json;charset=utf-8",
        #"Content-Length": "1926",
        "Origin": "http://localhost:8080",
        "Connection": "keep-alive",
        "Pragma":"no-cache",
        "Cache-Control":"no-cache"
        }
        url = 'http://127.0.0.1:8081/api/file-inputs/store'
        body = {
          "type": "fileInput",
          "id": 1,
          "name": ds_path,
          "fileName": ds_path,
          "separator": ",",
          "quoteChar": "\"",
          "escapeChar": "",
          "skipLines": 0,
          "strictQuotes": False,
          "ignoreLeadingWhiteSpace": True,
          "hasHeader": True,
          "skipDifferingLines": False,
          "comment": None,
          "nullValue": ""
        }
        r = requests.post(url, headers=headers, json=body)
        return r.content

        

In [10]:
# Inserisco tutti i ds dentro mypath in metanome
for name in [f for f in listdir(mypath) if isfile(join(mypath, f))]:
    post_ds("/home/marco/Scrivania/dep/backend/WEB-INF/classes/inputData/" + name)